In [1]:
import os
import collections
import re

# Local topography

**Note that the data source files are not on GitHub!**

They are in my `~/local` directory and also in the Dropbox folder with the Abegg files.

In [2]:
BASE = os.path.expanduser('C:/Users/jajacobs/Documents/ipynb/etcbc files/dss-master')
ORG = 'etcbc'
REPO = 'dss'
# VERSION = '0.1'

# REPO_DIR = f'{BASE}/{ORG}/{REPO}'
LOCAL = os.path.expanduser('C:/Users/jajacobs/Documents/ipynb/etcbc files/dss-master')

DATA_DIR = f'{LOCAL}'

META_DIR = f'{LOCAL}/sources/meta'

CHAR_TABLE = f'{META_DIR}/chars.txt'
MAN_TABLE = f'{META_DIR}/mans.txt'

# Sources

We have two source files:

* `dss_bib.txt` with biblical material
* `dss_nonbib.txt` with non-biblical material

Throughout this conversion program
we use `True` for the biblical material and `False` for the other material.

In [3]:
SOURCES = dict(
  bib=True,
  nonbib=False,
)

## Tables

We have two tables for mapping certain values in the source data to other values
in a systematic way:

* a manuscript table in order to represent mamuscript codes by their names.
  In most cases the name *is* the code.
* a character table relating unicode characters to their transliterations.

In [4]:
origFromTrans = {}
bookFromCode = {}

def readChars():
  with open(CHAR_TABLE, encoding = 'utf8') as fh:
    for line in fh:
      (orig, trans) = line.rstrip().split('\t')
      origFromTrans[trans] = orig
  print(f'{len(origFromTrans):>4} characters mapped')


def readBooks():
  with open(MAN_TABLE) as fh:
    for line in fh:
      (code, book) = line.rstrip().split('\t')
      bookFromCode[code] = book
  print(f'{len(bookFromCode):>4} mans mapped')
  
readChars()
readBooks()

  38 characters mapped
 265 mans mapped


# Slurp the data

We take in the data and store the lines in a dictionary of lists of lines,
keyed by the boolean "is biblical?"

In [5]:
lines = collections.defaultdict(list)

def getSourceLines():
    counter = 0

    for (src, isBib) in SOURCES.items():
        with open(f'{DATA_DIR}/{REPO}_{src}.txt', encoding='utf8') as fh:
            for line in fh:
                lines[isBib].append(line.strip())
        print(f'{src:<15}: {len(lines[isBib]):>5} lines')
        print(counter)
        counter += 1
    
getSourceLines()

bib            : 243157 lines
0
nonbib         : 378023 lines
1


In [6]:
print(f'{len(lines[False]):>5} lines')

378023 lines


# Parse lines

We read the stored lines and parse them.

If there are errors, we store all occurrences of them in a dict, keyed by:

* kind of error
* the sore point
* the source (`True` or `False` - biblical or not)

And then we get a list of list indices.

Later when we display the errors

* we replace `True` by `bib` and `False` by `nonbib`
* we display line numbers (one higher than list indices)
* we retrieve the corresponding source line

We only show at most `batch` many lines per error and per sore point and per source.

## Line splitting

We have to split lines differently in both sources.

source | separator | # fields
--- | --- | ---
bib | tab | 5
nonbib | space | 4

Several fields are made up of parts themselves.

**bib**

```Gen 1:19	1Q1 f1:1	w	w◊@Pc	32.5```

* `Gen` is book acronym
* `1` is the chapter
* `19` is the verse
* `1Q1` is the manuscript name
* `f1` *what is this called? folio, part, page?* - f = fragment, the number after the f is the column
* `1` *is the line?* - this is the line number
* `w` is the transcription
* `w◊` is the lexeme
* `Pc` is the morphology code
* `32` is the word number
* `5` *what is this? Sub-number, or part of the wordnumber?* - Accordance used a very irregular numbering system, but it essentially boils down to this: if the word number is followed by '.' with another number than the word is a particle of some kind. Sometimes the word number for a particle is the same number as the previous word but with an appended '.' with another number other

**nonbib**

```CD 1:2,3.1 ky k;Iy_2@Pc```

* `CD` is manuscript name
* `1` is column
* `2` is line
* `3` is line (again! are lines nested, is it a sub-line, *how shall I call it?*) - this is actually the word number. if it has a '.' and another number then the word is a particle that is bound to the following word.
* `ky` is transcription (this goes into the plain text)
* `k;ly_2` is lexeme, (*the `_2` is disambiguation?*) - this keys the lexeme to the lexicon entry when there are more than one
* `Pc` is morphology code

In [7]:
def splitLine(isBib, ln, line):
  parts = line.split('\t' if isBib else ' ')
  expFields = 5 if isBib else 4
  nFields = len(parts)
  if nFields != expFields:
    errors['wrong number of fields'][nFields][isBib].append(ln)
    return False
  return parts

In [8]:
errors = collections.defaultdict(
  lambda: collections.defaultdict(
    lambda: collections.defaultdict(list)
  )
)
batch = 78

def showErrors():
  for (kind, soreSources) in sorted(errors.items()):
    print(f'ERROR {kind}:')
    for (sore, srcOccs) in sorted(soreSources.items()):
      print(f'\t{sore}:')
      for (isBib, occs) in sorted(srcOccs.items()):
        nOccs = len(occs)
        srcStr = 'bib' if isBib else 'nonbib'
        print(f'\t\t{srcStr:<6}: {nOccs:>6}x:')
        for occ in occs[0:batch]:
          print(f'\t\t\t{occ + 1:>6} "{lines[isBib][occ]}"')
        if nOccs > batch:
          print('\t\t\t...')

def readData():
  for isBib in lines:
    for (i, line) in enumerate(lines[isBib]):
      if line.startswith('>'):
        continue
      parts = splitLine(isBib, i, line)
      if not parts:
        continue
    
readData()
showErrors()

ERROR wrong number of fields:
	1:
		nonbib:   1144x:
			 15051 "(fl)"
			 15053 "(fy)"
			 15799 "(fl)"
			 15801 "(fy)"
			 15807 "(fl)"
			 15809 "(fy)"
			 16153 "(fl)"
			 16155 "(fy)"
			 16843 "(fl)"
			 16845 "(fy)"
			 16932 "(fl)"
			 16934 "(fy)"
			 17056 "(fl)"
			 17058 "(fy)"
			 17321 "(fl)"
			 17323 "(fy)"
			 26788 "(fl)"
			 26790 "(fy)"
			 27862 "(fl)"
			 27864 "(fy)"
			 28642 "(fl)"
			 28644 "(fy)"
			 38697 "(fl)"
			 38699 "(fy)"
			 38715 "(fl)"
			 38717 "(fy)"
			 39051 "(fl)"
			 39053 "(fy)"
			 39281 "r"
			 39306 "(fl)"
			 39308 "(fy)"
			 39317 "(fl)"
			 39319 "(fy)"
			 50842 "(fl)"
			 50844 "(fy)"
			 51845 "r"
			 52434 "(fl)"
			 52436 "(fy)"
			 57629 "(fl)"
			 57631 "(fy)"
			 57713 "(f0)"
			 57715 "(fy)"
			 57727 "(fl)"
			 57729 "(fy)"
			 57799 "(f0)"
			 57801 "(fy)"
			 57827 "(fl)"
			 57829 "(fy)"
			 57844 "(fl)"
			 57846 "(fy)"
			 57849 "(f0)"
			 57851 "(fy)"
			 57871 "(f0)"

### Errors 1 - 39281 "r"

The characters "r" follows an interlinear line unless the interlinear line ends at the end of the line, then this character immediately precedes the interlinear line.

In [9]:
for line_num in errors['wrong number of fields'][1][False]:
    if 'r' in lines[False][line_num]:
        lines[False][line_num] = lines[False][line_num]+' - - - - -'
        print(line_num)

39280
51844
60238
64988
66135
67586
69034
70655
83163
83174
105507
105612
107921
108639
108662
108682
109294
112587
132292
137065
148644
151505
151707
151799
152005
152297
152838
152930
153291
160630
160659
160676
161413
188152
209559
213210
213341
213478
213567
219834
224175
226422
227154
227183
231974
232206
232603
232685
233133
233162
234509
234571
234950
240938
243160
246031
258486
258589
270009
270453
298961
298978
315083
322150
326578
326827
346333
347707
348413
368167
372844


### Errors 2 - Extra Space Between Words

> 13082 "1QSa 1:8,6.1" Some words in the manuscripts have extra space between them. These appear to be marked with one Ê per extra space that is found in Accordance. However, those extra spaces are not in the lines dict due to whitespace being stripped out I think. So, here we search for lines with a comma as the only lines with a comma that have this error are those lines that have the extra spaces in the original doc.

In [10]:
for line_num in errors['wrong number of fields'][2][False]:
    if ',' in lines[False][line_num]:
        lines[False][line_num] = lines[False][line_num]+' - -'

### Errors 3 - Empty or partial lines with no tag

> Here we find all lines that return error 3 (e.g. :     4486 "CD 13:17,13.1 [") and add the string 'NaN' to the end of the line, thus adding the fourth field required for non-biblical lines and filling it with NaN. All lines the return error 3 are either empty lines or partial lines that cannot receive a tag.

In [11]:
for line_num in errors['wrong number of fields'][3][False]:
    lines[False][line_num] = lines[False][line_num]+' -'
    print(line_num)

1
2
15
28
47
63
84
105
117
129
151
152
153
173
188
242
270
300
319
321
322
337
338
339
355
368
398
415
433
460
482
483
484
506
508
509
539
574
593
608
639
641
642
652
672
693
694
695
706
734
769
787
820
821
822
851
852
875
876
880
892
909
942
995
996
997
1013
1014
1015
1032
1052
1067
1094
1111
1139
1182
1183
1184
1212
1228
1245
1246
1247
1264
1278
1288
1300
1301
1302
1313
1352
1360
1375
1398
1410
1411
1412
1425
1439
1454
1455
1456
1484
1499
1506
1516
1538
1549
1581
1582
1583
1585
1586
1601
1634
1640
1641
1652
1670
1709
1710
1711
1727
1728
1729
1772
1773
1774
1792
1806
1807
1814
1856
1926
1942
1943
1961
1995
2009
2032
2033
2034
2056
2057
2081
2135
2147
2163
2164
2165
2182
2183
2184
2203
2204
2205
2213
2232
2233
2234
2259
2277
2293
2320
2372
2398
2411
2435
2436
2437
2444
2445
2466
2496
2530
2565
2566
2567
2580
2581
2602
2604
2605
2622
2623
2624
2637
2653
2703
2705
2706
2721
2763
2764
2765
2776
2799
2824
2836
2838
2839
2865
2866
2867
2890
2899
2900
2901
2948
2959
2960
2961
2983
2984
2998


19079
19080
19081
19083
19085
19087
19089
19091
19093
19094
19127
19128
19129
19137
19151
19168
19180
19208
19220
19228
19244
19267
19290
19303
19313
19328
19345
19357
19371
19383
19395
19406
19425
19427
19428
19442
19465
19466
19468
19470
19472
19474
19482
19494
19508
19520
19537
19553
19564
19577
19587
19620
19634
19636
19637
19653
19676
19702
19735
19776
19800
19827
19840
19842
19851
19858
19860
19869
19875
19876
19878
19880
19881
19883
19885
19887
19889
19891
19906
19920
19936
19971
19993
20022
20038
20062
20078
20089
20090
20091
20093
20094
20168
20186
20213
20235
20250
20265
20282
20317
20319
20321
20323
20325
20343
20367
20402
20414
20426
20459
20476
20496
20510
20535
20536
20541
20557
20569
20595
20613
20619
20623
20625
20627
20644
20666
20700
20725
20739
20758
20771
20799
20810
20811
20812
20840
20860
20874
20890
20904
20917
20942
20955
20956
20957
20961
20977
20979
20981
20983
20985
20987
20998
21019
21054
21061
21084
21115
21150
21172
21175
21187
21217
21232
21234
21294
2130

38687
38691
38692
38694
38703
38711
38727
38738
38751
38764
38765
38767
38771
38773
38780
38782
38787
38789
38794
38795
38797
38800
38802
38804
38810
38812
38817
38819
38824
38826
38831
38832
38834
38847
38862
38875
38888
38897
38942
38944
38970
38972
38979
38980
38982
38989
38990
39002
39004
39006
39011
39013
39020
39022
39026
39027
39029
39035
39037
39044
39046
39056
39058
39062
39063
39065
39069
39070
39072
39077
39079
39084
39085
39087
39092
39094
39097
39099
39100
39102
39106
39108
39112
39113
39115
39121
39123
39125
39146
39171
39179
39181
39187
39188
39190
39196
39198
39200
39204
39206
39207
39209
39214
39216
39218
39223
39225
39231
39233
39238
39239
39241
39249
39250
39275
39282
39319
39339
39340
39342
39351
39352
39354
39360
39362
39366
39367
39369
39373
39375
39382
39384
39396
39401
39403
39409
39411
39417
39419
39423
39424
39426
39437
39439
39449
39450
39460
39467
39469
39475
39489
39495
39497
39503
39505
39512
39514
39519
39521
39525
39526
39528
39533
39535
39541
39542
3954

50513
50514
50516
50520
50522
50526
50527
50529
50534
50536
50546
50559
50575
50576
50577
50605
50628
50646
50657
50667
50681
50691
50700
50708
50717
50724
50734
50741
50742
50744
50748
50757
50768
50777
50782
50788
50796
50809
50817
50819
50830
50839
50848
50850
50854
50855
50857
50864
50866
50873
50875
50879
50880
50882
50887
50889
50891
50897
50899
50901
50907
50909
50911
50913
50915
50916
50918
50922
50924
50926
50930
50931
50933
50939
50941
50948
50950
50954
50955
50957
50961
50963
50970
50972
50974
50984
50986
50991
50993
50997
50998
51000
51004
51006
51012
51014
51018
51019
51021
51025
51027
51030
51032
51034
51038
51039
51046
51058
51069
51081
51083
51085
51087
51089
51090
51094
51095
51097
51103
51105
51111
51115
51117
51118
51120
51124
51126
51134
51136
51144
51146
51151
51152
51154
51159
51161
51163
51168
51170
51172
51180
51181
51183
51185
51193
51194
51196
51198
51206
51208
51214
51216
51218
51224
51225
51227
51231
51233
51244
51246
51253
51255
51263
51265
51270
51271
5127

60216
60220
60222
60224
60228
60231
60237
60239
60243
60244
60246
60250
60252
60254
60257
60259
60261
60265
60267
60271
60272
60274
60277
60279
60281
60285
60287
60291
60293
60297
60298
60300
60304
60306
60311
60312
60314
60318
60320
60324
60325
60327
60331
60332
60334
60339
60341
60346
60348
60352
60354
60358
60359
60361
60365
60367
60371
60373
60377
60379
60383
60384
60386
60388
60391
60399
60408
60424
60428
60436
60437
60438
60460
60470
60473
60475
60478
60499
60521
60539
60546
60561
60567
60569
60571
60576
60577
60579
60581
60583
60589
60595
60599
60602
60605
60607
60614
60620
60626
60628
60635
60643
60646
60647
60648
60654
60666
60668
60670
60671
60676
60678
60682
60683
60685
60690
60692
60698
60700
60702
60703
60713
60714
60716
60727
60729
60732
60742
60744
60749
60760
60761
60763
60769
60778
60779
60784
60793
60805
60806
60816
60820
60831
60832
60843
60844
60857
60858
60868
60869
60878
60882
60883
60893
60903
60910
60916
60917
60923
60931
60938
60939
60941
60946
60954
60963
6096

...

322708
322710
322713
322715
322716
322718
322722
322724
322727
322729
322731
322735
322736
322738
322741
322743
322745
322749
322750
322752
322756
322758
322762
322764
322768
322770
322771
322773
322777
322779
322784
322785
322787
322791
322793
322797
322798
322800
322804
322805
322807
322811
322813
322817
322818
322820
322823
322825
322827
322831
322832
322834
322840
322842
322846
322847
322849
322853
322855
322859
322860
322862
322866
322868
322870
322874
322875
322877
322881
322882
322884
322886
322889
322890
322892
322894
322898
322899
322901
322905
322906
322908
322910
322913
322914
322916
322921
322922
322924
322926
322929
322931
322935
322936
322938
322942
322943
322945
322948
322950
322951
322953
322957
322958
322960
322964
322965
322967
322971
322972
322974
322979
322980
322982
322984
322988
322989
322991
322997
322999
323003
323004
323009
323014
323017
323018
323020
323024
323026
323030
323031
323033
323037
323039
323044
323046
323052
323054
323059
323060
323062
323066
323068

332043
332046
332047
332049
332050
332052
332055
332057
332059
332062
332064
332065
332067
332070
332072
332073
332075
332080
332081
332083
332087
332089
332099
332101
332124
332125
332126
332128
332130
332158
332159
332163
332172
332180
332181
332183
332185
332187
332189
332191
332195
332197
332198
332200
332203
332209
332213
332220
332221
332223
332229
332231
332235
332236
332238
332244
332245
332247
332249
332253
332255
332259
332260
332262
332264
332268
332270
332275
332276
332278
332284
332286
332290
332291
332293
332298
332300
332305
332306
332308
332312
332314
332318
332319
332321
332325
332327
332332
332333
332335
332337
332339
332341
332342
332344
332346
332350
332351
332353
332358
332360
332364
332365
332367
332371
332373
332377
332378
332380
332382
332385
332387
332389
332392
332393
332395
332401
332402
332404
332408
332409
332411
332415
332417
332421
332423
332427
332428
332430
332432
332436
332437
332439
332445
332447
332449
332453
332454
332456
332460
332461
332463
332468

343366
343368
343378
343380
343394
343395
343399
343409
343410
343411
343449
343472
343473
343475
343479
343481
343483
343484
343516
343550
343551
343556
343560
343561
343563
343567
343569
343574
343576
343580
343581
343583
343586
343588
343590
343593
343595
343597
343601
343602
343604
343606
343610
343612
343617
343619
343623
343624
343626
343632
343634
343637
343638
343640
343642
343648
343650
343697
343732
343743
343762
343786
343835
343848
343861
343880
343889
343905
343921
343925
343961
343977
343978
343997
344009
344011
344017
344027
344037
344040
344051
344053
344067
344070
344089
344094
344103
344113
344115
344119
344125
344130
344135
344137
344140
344146
344153
344161
344170
344182
344184
344188
344190
344196
344200
344204
344209
344213
344218
344224
344226
344230
344232
344236
344237
344239
344245
344247
344253
344255
344261
344263
344267
344268
344270
344274
344276
344278
344279
344281
344283
344288
344290
344295
344297
344302
344303
344305
344309
344311
344316
344318
344323

362743
362782
362784
362785
362826
362838
362839
362840
362851
362863
362894
362916
362930
362944
362945
362954
362959
362977
362996
362997
363012
363023
363031
363038
363045
363076
363077
363078
363095
363119
363129
363130
363131
363148
363161
363204
363236
363256
363277
363278
363279
363308
363332
363346
363361
363383
363397
363398
363399
363420
363421
363422
363436
363461
363475
363508
363518
363538
363554
363598
363607
363608
363609
363624
363625
363638
363640
363641
363670
363696
363714
363732
363758
363760
363761
363808
363817
363832
363843
363865
363873
363874
363875
363876
363920
363940
363951
363965
363966
363967
363996
364014
364015
364016
364049
364064
364087
364088
364089
364106
364111
364132
364144
364145
364146
364163
364188
364207
364208
364209
364232
364233
364234
364290
364291
364292
364333
364345
364381
364384
364396
364397
364399
364436
364471
364500
364515
364516
364517
364559
364569
364582
364603
364617
364632
364633
364634
364640
364641
364652
364653
364654
364657

373740
373742
373746
373747
373749
373754
373760
373764
373766
373770
373772
373774
373779
373780
373782
373784
373788
373790
373794
373795
373797
373799
373800
373803
373804
373806
373808
373813
373814
373816
373818
373822
373824
373829
373831
373836
373838
373842
373843
373845
373849
373850
373852
373854
373856
373858
373860
373866
373867
373869
373871
373875
373877
373883
373885
373889
373890
373892
373897
373899
373906
373908
373913
373914
373916
373920
373922
373927
373928
373930
373932
373934
373936
373938
373942
373943
373945
373947
373951
373953
373959
373960
373962
373969
373971
373976
373977
373979
373983
373985
373989
373990
373992
373995
373997
373998
374002
374004
374005
374007
374010
374012
374014
374019
374021
374025
374026
374028
374030
374036
374038
374042
374043
374047
374053
374055
374059
374063
374066
374068
374073
374075
374079
374080
374082
374084
374088
374090
374094
374095
374097
374101
374102
374104
374105
374107
374111
374112
374114
374118
374120
374125
374126

### Error 5: two spaces in a row

> There is one occurance of a nonbiblical line having two spaces in a row: 256841 "4Q491 f36:2,4.1 [\\]  \\\@0". Here, I remove the extra space.

In [12]:
for line_num in errors['wrong number of fields'][5][False]:
    lines[False][line_num] = lines[False][line_num][:(lines[False][line_num].index('  '))]+lines[False][line_num][(lines[False][line_num].index('  '))+1:]

### Error 6: two tabs in a row

> There is one occurance of a biblical line having two tabs in a row after the morph tag slot: "208179 "8Q3 f12_16:17	8Q3 f12_16:17	--	\@0		949". Here, I remove the extra tab.

In [13]:
for line_num in errors['wrong number of fields'][6][True]:
    lines[True][line_num] = lines[True][line_num][:(lines[True][line_num].index('\t\t'))]+lines[True][line_num][(lines[True][line_num].index('\t\t'))+1:]

### Lines without Morph Tag step 1

> Some lines do not have a lexeme or morph tag, here we add two blank columns filled with ' -'

In [14]:
for line in lines[False]:
    if not '@' in line and not '%' in line:
        lines[False][lines[False].index(line)] = line + ' -'

In [15]:
for line in lines[True]:
    if not '@' in line and not '%' in line:
        lines[True][lines[True].index(line)] = line + ' - -'

In [ ]:
with open('dss_nonbib_errors_fixed_step_1.txt', 'w', encoding='utf8') as f:
    for line in lines[False]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass
        
with open('dss_bib_errors_fixed_step_1.txt', 'w', encoding='utf8') as f:
    for line in lines[True]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass

### Word Numbers step 2

> Remove word numbers, add new column that marks words bound to the next word with 'B'

In [16]:
for line in lines[False]:
    # ignore lines that are placed at the beginning of scroll line
    if line.startswith('>'):
        print(line)
        pass

    else:
        try:
                # set pattern to match any number of characters before a comma (scroll name + frag num + line num)
            p = re.compile('.*?\,\d+')
            
                # match the pattern to the line and store in variable s1_s
            s1_s = p.match(line).group(0)
            
            try:
                    # try to match the pattern to line + 1 and store in s2_s
                s2_s = p.match(lines[False][lines[False].index(line)+1]).group(0)
            except:
                    # if the pattern is not matched (e.g. line + 1 is the beginning of a new scroll line)
                s2_s = ''
            
                # compare s1_2 and s2_s. 

            if s1_s == s2_s:
                    # if they are the same, remove the word number
                line_update1 = re.sub('\,\d+\.\d+', '', line)
                    # and add ' B'
                lines[False][lines[False].index(line)] = line_update1 + ' B'

            else:
                    # if they are different, remove the word number
                line_update3 = re.sub('\,\d+\.\d+', '', line)
                    # and add ' -'
                lines[False][lines[False].index(line)] = line_update3 + ' -'
        except (AttributeError, IndexError) as e:
            pass

>CD 1:1 -
>CD 1:2 -
>CD 1:3 -
>CD 1:4 -
>CD 1:5 -
>CD 1:6 -
>CD 1:7 -
>CD 1:8 -
>CD 1:9 -
>CD 1:10 -
>CD 1:11 -
>CD 1:12 -
>CD 1:13 -
>CD 1:14 -
>CD 1:15 -
>CD 1:16 -
>CD 1:17 -
>CD 1:18 -
>CD 1:19 -
>CD 1:20 -
>CD 1:21 -
>CD 2:1 -
>CD 2:2 -
>CD 2:3 -
>CD 2:4 -
>CD 2:5 -
>CD 2:6 -
>CD 2:7 -
>CD 2:8 -
>CD 2:9 -
>CD 2:10 -
>CD 2:11 -
>CD 2:12 -
>CD 2:13 -
>CD 2:14 -
>CD 2:15 -
>CD 2:16 -
>CD 2:17 -
>CD 2:18 -
>CD 2:19 -
>CD 2:20 -
>CD 2:21 -
>CD 3:1 -
>CD 3:2 -
>CD 3:3 -
>CD 3:4 -
>CD 3:5 -
>CD 3:6 -
>CD 3:7 -
>CD 3:8 -
>CD 3:9 -
>CD 3:10 -
>CD 3:11 -
>CD 3:12 -
>CD 3:13 -
>CD 3:14 -
>CD 3:15 -
>CD 3:16 -
>CD 3:17 -
>CD 3:18 -
>CD 3:19 -
>CD 3:20 -
>CD 3:21 -
>CD 4:1 -
>CD 4:2 -
>CD 4:3 -
>CD 4:4 -
>CD 4:5 -
>CD 4:6 -
>CD 4:7 -
>CD 4:8 -
>CD 4:9 -
>CD 4:10 -
>CD 4:11 -
>CD 4:12 -
>CD 4:13 -
>CD 4:14 -
>CD 4:15 -
>CD 4:16 -
>CD 4:17 -
>CD 4:18 -
>CD 4:19 -
>CD 4:20 -
>CD 4:21 -
>CD 5:1 -
>CD 5:2 -
>CD 5:3 -
>CD 5:4 -
>CD 5:5 -
>CD 5:6 -
>CD 5:7 -
>CD 5:8 -
>CD 5:9 -
>CD 5:10 -
>CD 5:11 -


>1QSa 1:24 -
>1QSa 1:25 -
>1QSa 1:26 -
>1QSa 1:27 -
>1QSa 1:28 -
>1QSa 1:29 -
>1QSa 2:1 -
>1QSa 2:2 -
>1QSa 2:3 -
>1QSa 2:4 -
>1QSa 2:5 -
>1QSa 2:6 -
>1QSa 2:7 -
>1QSa 2:8 -
>1QSa 2:9 -
>1QSa 2:10 -
>1QSa 2:11 -
>1QSa 2:12 -
>1QSa 2:13 -
>1QSa 2:14 -
>1QSa 2:15 -
>1QSa 2:16 -
>1QSa 2:17 -
>1QSa 2:18 -
>1QSa 2:19 -
>1QSa 2:20 -
>1QSa 2:21 -
>1QSa 2:22 -
>1QSb 1:1 -
>1QSb 1:2 -
>1QSb 1:3 -
>1QSb 1:4 -
>1QSb 1:5 -
>1QSb 1:6 -
>1QSb 1:7 -
>1QSb 1:8 -
>1QSb 1:9 -
>1QSb 1:10 -
>1QSb 1:26 -
>1QSb 1:27 -
>1QSb 1:28 -
>1QSb 2:1 -
>1QSb 2:2 -
>1QSb 2:3 -
>1QSb 2:4 -
>1QSb 2:5 -
>1QSb 2:22 -
>1QSb 2:23 -
>1QSb 2:24 -
>1QSb 2:25 -
>1QSb 2:26 -
>1QSb 2:27 -
>1QSb 2:28 -
>1QSb 3:1 -
>1QSb 3:2 -
>1QSb 3:3 -
>1QSb 3:4 -
>1QSb 3:5 -
>1QSb 3:6 -
>1QSb 3:7 -
>1QSb 3:8 -
>1QSb 3:9 -
>1QSb 3:17 -
>1QSb 3:18 -
>1QSb 3:19 -
>1QSb 3:20 -
>1QSb 3:21 -
>1QSb 3:22 -
>1QSb 3:23 -
>1QSb 3:24 -
>1QSb 3:25 -
>1QSb 3:26 -
>1QSb 3:27 -
>1QSb 3:28 -
>1QSb 4:1 -
>1QSb 4:2 -
>1QSb 4:3 -
>1QSb 4:4 -
>1QSb 4:5 -
>1QSb 4:20

>1QM 16:17 -
>1QM 16:18 -
>1QM 16:19 -
>1QM 16:20 -
>1QM 17:1 -
>1QM 17:2 -
>1QM 17:3 -
>1QM 17:4 -
>1QM 17:5 -
>1QM 17:6 -
>1QM 17:7 -
>1QM 17:8 -
>1QM 17:9 -
>1QM 17:10 -
>1QM 17:11 -
>1QM 17:12 -
>1QM 17:13 -
>1QM 17:14 -
>1QM 17:15 -
>1QM 17:16 -
>1QM 17:17 -
>1QM 17:18 -
>1QM 17:19 -
>1QM 17:20 -
>1QM 18:1 -
>1QM 18:2 -
>1QM 18:3 -
>1QM 18:4 -
>1QM 18:5 -
>1QM 18:6 -
>1QM 18:7 -
>1QM 18:8 -
>1QM 18:9 -
>1QM 18:10 -
>1QM 18:11 -
>1QM 18:12 -
>1QM 18:13 -
>1QM 18:14 -
>1QM 18:15 -
>1QM 18:16 -
>1QM 18:17 -
>1QM 18:18 -
>1QM 18:19 -
>1QM 18:20 -
>1QM 19:1 -
>1QM 19:2 -
>1QM 19:3 -
>1QM 19:4 -
>1QM 19:5 -
>1QM 19:6 -
>1QM 19:7 -
>1QM 19:8 -
>1QM 19:9 -
>1QM 19:10 -
>1QM 19:11 -
>1QM 19:12 -
>1QM 19:13 -
>1QM 19:14 -
>1QM 20:8 -
>1QM f3:1 -
>1QM f3:2 -
>1QM f7:1 -
>1QHa 2:12 -
>1QHa 2:13 -
>1QHa 2:14 -
>1QHa 2:15 -
>1QHa 2:16 -
>1QHa 2:24 -
>1QHa 2:25 -
>1QHa 2:26 -
>1QHa 2:27 -
>1QHa 2:28 -
>1QHa 2:29 -
>1QHa 2:30 -
>1QHa 2:31 -
>1QHa 2:32 -
>1QHa 3:15 -
>1QHa 3:16 -
>1QHa 3:17 -
>1QH

>1QHa 18:37 -
>1QHa 18:38 -
>1QHa 18:39 -
>1QHa 18:40 -
>1QHa 18:41 -
>1QHa 19:4 -
>1QHa 19:5 -
>1QHa 19:6 -
>1QHa 19:7 -
>1QHa 19:8 -
>1QHa 19:9 -
>1QHa 19:10 -
>1QHa 19:11 -
>1QHa 19:12 -
>1QHa 19:13 -
>1QHa 19:14 -
>1QHa 19:15 -
>1QHa 19:16 -
>1QHa 19:17 -
>1QHa 19:18 -
>1QHa 19:19 -
>1QHa 19:20 -
>1QHa 19:21 -
>1QHa 19:22 -
>1QHa 19:23 -
>1QHa 19:24 -
>1QHa 19:25 -
>1QHa 19:26 -
>1QHa 19:27 -
>1QHa 19:28 -
>1QHa 19:29 -
>1QHa 19:30 -
>1QHa 19:31 -
>1QHa 19:32 -
>1QHa 19:33 -
>1QHa 19:34 -
>1QHa 19:35 -
>1QHa 19:36 -
>1QHa 19:37 -
>1QHa 19:38 -
>1QHa 19:39 -
>1QHa 19:40 -
>1QHa 19:41 -
>1QHa 19:42 -
>1QHa 20:4 -
>1QHa 20:5 -
>1QHa 20:6 -
>1QHa 20:7 -
>1QHa 20:8 -
>1QHa 20:9 -
>1QHa 20:10 -
>1QHa 20:11 -
>1QHa 20:12 -
>1QHa 20:13 -
>1QHa 20:14 -
>1QHa 20:15 -
>1QHa 20:16 -
>1QHa 20:17 -
>1QHa 20:18 -
>1QHa 20:19 -
>1QHa 20:20 -
>1QHa 20:21 -
>1QHa 20:22 -
>1QHa 20:23 -
>1QHa 20:24 -
>1QHa 20:25 -
>1QHa 20:26 -
>1QHa 20:27 -
>1QHa 20:28 -
>1QHa 20:29 -
>1QHa 20:30 -
>1QHa 20:31 -
>1QH

>1Q20 6:2 -
>1Q20 6:3 -
>1Q20 6:4 -
>1Q20 6:5 -
>1Q20 6:6 -
>1Q20 6:7 -
>1Q20 6:8 -
>1Q20 6:9 -
>1Q20 6:10 -
>1Q20 6:11 -
>1Q20 6:12 -
>1Q20 6:13 -
>1Q20 6:14 -
>1Q20 6:15 -
>1Q20 6:16 -
>1Q20 6:17 -
>1Q20 6:18 -
>1Q20 6:19 -
>1Q20 6:20 -
>1Q20 6:21 -
>1Q20 6:22 -
>1Q20 6:23 -
>1Q20 6:24 -
>1Q20 6:25 -
>1Q20 6:26 -
>1Q20 6:27 -
>1Q20 7:1 -
>1Q20 7:2 -
>1Q20 7:3 -
>1Q20 7:4 -
>1Q20 7:5 -
>1Q20 7:6 -
>1Q20 7:7 -
>1Q20 7:8 -
>1Q20 7:9 -
>1Q20 7:10 -
>1Q20 7:11 -
>1Q20 7:12 -
>1Q20 7:13 -
>1Q20 7:14 -
>1Q20 7:15 -
>1Q20 7:16 -
>1Q20 7:17 -
>1Q20 7:18 -
>1Q20 7:19 -
>1Q20 7:20 -
>1Q20 7:21 -
>1Q20 7:22 -
>1Q20 7:23 -
>1Q20 8:1 -
>1Q20 8:2 -
>1Q20 8:3 -
>1Q20 8:4 -
>1Q20 8:5 -
>1Q20 8:6 -
>1Q20 8:7 -
>1Q20 8:8 -
>1Q20 8:9 -
>1Q20 10:1 -
>1Q20 10:2 -
>1Q20 10:3 -
>1Q20 10:4 -
>1Q20 10:5 -
>1Q20 10:6 -
>1Q20 10:7 -
>1Q20 10:8 -
>1Q20 10:9 -
>1Q20 10:10 -
>1Q20 10:11 -
>1Q20 10:12 -
>1Q20 10:13 -
>1Q20 10:14 -
>1Q20 10:15 -
>1Q20 10:16 -
>1Q20 10:17 -
>1Q20 10:18 -
>1Q20 11:1 -
>1Q20 11:2 -
>1Q

...

>11Q19 11:14 -
>11Q19 11:15 -
>11Q19 11:16 -
>11Q19 12:8 -
>11Q19 12:9 -
>11Q19 12:10 -
>11Q19 12:11 -
>11Q19 12:12 -
>11Q19 12:13 -
>11Q19 12:14 -
>11Q19 12:15 -
>11Q19 12:16 -
>11Q19 13:1 -
>11Q19 13:2 -
>11Q19 13:3 -
>11Q19 13:4 -
>11Q19 13:5 -
>11Q19 13:6 -
>11Q19 13:7 -
>11Q19 13:8 -
>11Q19 13:9 -
>11Q19 13:10 -
>11Q19 13:11 -
>11Q19 13:11 -
>11Q19 13:12 -
>11Q19 13:12 -
>11Q19 13:13 -
>11Q19 13:14 -
>11Q19 13:15 -
>11Q19 13:16 -
>11Q19 13:17 -
>11Q19 14:0 -
>11Q19 14:1 -
>11Q19 14:2 -
>11Q19 14:3 -
>11Q19 14:4 -
>11Q19 14:5 -
>11Q19 14:6 -
>11Q19 14:7 -
>11Q19 14:8 -
>11Q19 14:9 -
>11Q19 14:10 -
>11Q19 14:11 -
>11Q19 14:12 -
>11Q19 14:13 -
>11Q19 14:14 -
>11Q19 14:15 -
>11Q19 14:16 -
>11Q19 14:17 -
>11Q19 14:18 -
>11Q19 15:1 -
>11Q19 15:2 -
>11Q19 15:3 -
>11Q19 15:3 -
>11Q19 15:4 -
>11Q19 15:5 -
>11Q19 15:6 -
>11Q19 15:7 -
>11Q19 15:8 -
>11Q19 15:9 -
>11Q19 15:10 -
>11Q19 15:11 -
>11Q19 15:12 -
>11Q19 15:13 -
>11Q19 15:14 -
>11Q19 15:15 -
>11Q19 15:16 -
>11Q19 15:17 -
>11Q19 15:1

>11Q19 48:5 -
>11Q19 48:6 -
>11Q19 48:7 -
>11Q19 48:8 -
>11Q19 48:9 -
>11Q19 48:10 -
>11Q19 48:11 -
>11Q19 48:12 -
>11Q19 48:13 -
>11Q19 48:14 -
>11Q19 48:15 -
>11Q19 48:16 -
>11Q19 48:17 -
>11Q19 49:1 -
>11Q19 49:2 -
>11Q19 49:3 -
>11Q19 49:4 -
>11Q19 49:5 -
>11Q19 49:6 -
>11Q19 49:7 -
>11Q19 49:8 -
>11Q19 49:9 -
>11Q19 49:10 -
>11Q19 49:11 -
>11Q19 49:12 -
>11Q19 49:13 -
>11Q19 49:14 -
>11Q19 49:15 -
>11Q19 49:16 -
>11Q19 49:17 -
>11Q19 49:18 -
>11Q19 49:19 -
>11Q19 49:20 -
>11Q19 49:21 -
>11Q19 50:1 -
>11Q19 50:2 -
>11Q19 50:3 -
>11Q19 50:4 -
>11Q19 50:5 -
>11Q19 50:6 -
>11Q19 50:7 -
>11Q19 50:8 -
>11Q19 50:9 -
>11Q19 50:10 -
>11Q19 50:11 -
>11Q19 50:12 -
>11Q19 50:13 -
>11Q19 50:14 -
>11Q19 50:15 -
>11Q19 50:16 -
>11Q19 50:17 -
>11Q19 50:18 -
>11Q19 50:19 -
>11Q19 50:20 -
>11Q19 50:21 -
>11Q19 51:1 -
>11Q19 51:2 -
>11Q19 51:3 -
>11Q19 51:4 -
>11Q19 51:5 -
>11Q19 51:6 -
>11Q19 51:7 -
>11Q19 51:8 -
>11Q19 51:9 -
>11Q19 51:10 -
>11Q19 51:11 -
>11Q19 51:12 -
>11Q19 51:13 -
>11Q19 51:14

>11Q20 15:1 -
>11Q20 15:2 -
>11Q20 15:3 -
>11Q20 15:4 -
>11Q20 15:5 -
>11Q20 15:6 -
>11Q20 15:7 -
>11Q20 15:8 -
>11Q20 16:1 -
>11Q20 16:2 -
>11Q20 16:3 -
>11Q20 16:4 -
>11Q20 16:5 -
>11Q20 16:6 -
>11Q20 16:7 -
>11Q20 f31:1 -
>11Q20 f31:2 -
>11Q20 f31:3 -
>11Q20 f31:4 -
>11Q20 f31:5 -
>11Q20 f32:1 -
>11Q20 f32:2 -
>11Q20 f32:3 -
>11Q20 f33:1 -
>11Q20 f33:2 -
>11Q20 f33:3 -
>11Q20 f33:4 -
>11Q20 f34:1 -
>11Q20 f34:2 -
>11Q20 f35:1 -
>11Q20 f35:2 -
>11Q20 f36:1 -
>11Q20 f36:2 -
>11Q20 f37:1 -
>11Q20 f37:2 -
>11Q20 f37:3 -
>11Q20 f38:1 -
>11Q20 f39:1 -
>11Q20 f40:1 -
>11Q20 f41:1 -
>11Q20 f42:1 -
>11Q21 f1:1 -
>11Q21 f1:2 -
>11Q21 f1:3 -
>11Q21 f1:4 -
>11Q21 f1:5 -
>11Q21 f1:6 -
>11Q21 f2:1 -
>11Q21 f2:2 -
>11Q21 f2:3 -
>11Q21 f2:4 -
>11Q21 f3:1 -
>11Q21 f3:2 -
>11Q21 f3:3 -
>11Q21 f3:4 -
>11Q21 f3:5 -
>11Q22 f1:1 -
>11Q22 f1:2 -
>11Q22 f1:3 -
>11Q22 f2:1 -
>11Q22 f2:2 -
>11Q22 f3:1 -
>11Q22 f3:2 -
>11Q22 f4:1 -
>11Q22 f5:1 -
>11Q22 f6:1 -
>11Q22 f6:2 -
>11Q22 f7:1 -
>11Q22 f7:2 -
>11Q23 f

>PAM43677 f20:2 -
>PAM43677 f20:3 -
>PAM43677 f22:1 -
>PAM43677 f22:2 -
>PAM43677 f22:3 -
>PAM43677 f22:4 -
>PAM43677 f25:1 -
>PAM43677 f25:2 -
>PAM43677 f26:1 -
>PAM43677 f26:2 -
>PAM43677 f27:1 -
>PAM43677 f27:2 -
>PAM43677 f27:3 -
>PAM43677 f29:1 -
>PAM43677 f29:2 -
>PAM43677 f29:3 -
>PAM43677 f34:1 -
>PAM43677 f34:2 -
>PAM43677 f37:1 -
>PAM43677 f37:2 -
>PAM43677 f37:3 -
>PAM43677 f39:1 -
>PAM43677 f39:2 -
>PAM43677 f39:3 -
>PAM43677 f40:1 -
>PAM43677 f42:1 -
>PAM43677 f42:2 -
>PAM43678 f1:1 -
>PAM43678 f1:2 -
>PAM43678 f1:3 -
>PAM43678 f2:1 -
>PAM43678 f2:2 -
>PAM43678 f2:3 -
>PAM43678 f4:1 -
>PAM43678 f4:2 -
>PAM43678 f4:3 -
>PAM43678 f5:1 -
>PAM43678 f6:1 -
>PAM43678 f6:2 -
>PAM43678 f6:3 -
>PAM43678 f6:4 -
>PAM43678 f6:5 -
>PAM43678 f7:1 -
>PAM43678 f7:2 -
>PAM43678 f7:3 -
>PAM43678 f7:4 -
>PAM43678 f8:1 -
>PAM43678 f8:2 -
>PAM43678 f8:3 -
>PAM43678 f9:1 -
>PAM43678 f9:2 -
>PAM43678 f10:1 -
>PAM43678 f11:1 -
>PAM43678 f11:2 -
>PAM43678 f11:3 -
>PAM43678 f12:1 -
>PAM43678 f12:2 

>PAM43690 f35:1 -
>PAM43690 f35:2 -
>PAM43690 f35:3 -
>PAM43690 f35:4 -
>PAM43690 f37:1 -
>PAM43690 f37:2 -
>PAM43690 f39:1 -
>PAM43690 f50:1 -
>PAM43690 f64:1 -
>PAM43690 f67:1 -
>PAM43691 f2:1 -
>PAM43691 f2:2 -
>PAM43691 f2:3 -
>PAM43691 f2:4 -
>PAM43691 f5:1 -
>PAM43691 f5:2 -
>PAM43691 f5:3 -
>PAM43691 f8:1 -
>PAM43691 f8:2 -
>PAM43691 f8:3 -
>PAM43691 f9:1 -
>PAM43691 f9:2 -
>PAM43691 f9:3 -
>PAM43691 f9:4 -
>PAM43691 f11:1 -
>PAM43691 f11:2 -
>PAM43691 f13:1 -
>PAM43691 f13:2 -
>PAM43691 f17:1 -
>PAM43691 f17:2 -
>PAM43691 f19:1 -
>PAM43691 f22:1 -
>PAM43691 f22:2 -
>PAM43691 f40:1 -
>PAM43691 f40:2 -
>PAM43691 f40:3 -
>PAM43691 f43:1 -
>PAM43691 f43:2 -
>PAM43691 f53:1 -
>PAM43691 f53:2 -
>PAM43691 f54:1 -
>PAM43691 f54:2 -
>PAM43691 f57:1 -
>PAM43692 f1:1 -
>PAM43692 f3:1 -
>PAM43692 f3:2 -
>PAM43692 f4:1 -
>PAM43692 f4:2 -
>PAM43692 f4:3 -
>PAM43692 f9:1 -
>PAM43692 f9:2 -
>PAM43692 f9:3 -
>PAM43692 f13:1 -
>PAM43692 f21:1 -
>PAM43692 f21:2 -
>PAM43692 f22:1 -
>PAM43692 f25:1

In [17]:
for line in lines[True]:
    p = re.compile('\t\d+\.?\d?')
    word_number = p.findall(line)[-1]

    if '.' in word_number:
        lines[True][lines[True].index(line)] = re.sub('\d+\.\d', 'B', line)
    else:
        lines[True][lines[True].index(line)] = re.sub(word_number, '\t-', line)

In [ ]:
with open('dss_nonbib_errors_fixed_step_2.txt', 'w', encoding='utf8') as f:
    for line in lines[False]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass
        
with open('dss_bib_errors_fixed_step_2.txt', 'w', encoding='utf8') as f:
    for line in lines[True]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass

### Errors 2 - Interlinear lines step 3

> Interlinear lines or words are marked with (a) or in two cases where two lines are interlinear a (b) for the second oen. The line/word will be preceded by "e(s9).(xb5). (a)" and the end of the line/word will be followed by "r"
> interate through each line. Create flag - interlinear = false. Triggered to true if line contains "e(s9).(xb5). (a)" or "e(s9).(xb5). (b)" triggered to false at escr and end of line. Add '-' if false, add ' s1' or ' s2' if true.

In [18]:
is_s = '-'

for line in lines[False]:
    if line.startswith('>'):
        is_s = '-'

    elif '. (a)' in line:
        is_s = 's1'

    elif '. (b)' in line:
        is_s = 's2'

    elif 'r' in line:
        is_s = '-'

    else:
        if is_s == '-':
            lines[False][lines[False].index(line)] = line + ' -'
        elif is_s == 's1':
            lines[False][lines[False].index(line)] = line + ' s1'
        else:
            lines[False][lines[False].index(line)] = line + ' s2'


In [ ]:
with open('dss_nonbib_errors_fixed_step_3.txt', 'w', encoding='utf8') as f:
    for line in lines[False]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass
        
with open('dss_bib_errors_fixed_step_3.txt', 'w', encoding='utf8') as f:
    for line in lines[True]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass

 ### Errors 1 - Different Fonts in non-biblical texts step 4

> Error mostly contains lines that are wrapped around words that appear in the Accordance data in a font other than Yehudit. The most common is Lachish '(Fl)' which is used for words that are written in Paleo-Hebrew. Here we replace the wrapper lines with the string 'remove 2 3 4' to tag it for removal at the end of the error cleansing process. The line needs to remain until the end of the process so that the indexing of lines remains keyed to the indexing of the errors. Then, we add the string 'PH' (Paleo-Hebrew) to the end of the Paleo-Hebrew line as an additional tag for words wrapped in '(Pl)'. For words wrapped in '(F0)' we append 'F0' to the end of the tagged as a place holder until I figure out what font (F0) stands for. (FT) only occurs in four lines, not sure what it stands for. But I think it sets the font for the entire line. Here, I add (FT) to the tag of the first word with a tag and delete the line setting the font (note that this error occurs in Errors 2).

In [19]:
font = '-'

for line in lines[False]:
    if line.startswith('>'):
        font = '-'

    elif '(fl)' in line:
        font = 'PH'

    elif '(fy)' in line:
        font = '-'

    elif '(f0)' in line:
        font = 'f0'
        
    elif '(ft)' in line:
        font = 'FT'

    else:
        if font == 'PH':
            lines[False][lines[False].index(line)] = line + ' PH'
        elif font == 'f0':
            lines[False][lines[False].index(line)] = line + ' F0'
        elif font == 'ft':
            lines[False][lines[False].index(line)] = line + ' FT'            
        else:
            lines[False][lines[False].index(line)] = line + ' -'

In [ ]:
with open('dss_nonbib_errors_fixed_step_4.txt', 'w', encoding='utf8') as f:
    for line in lines[False]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass
        
with open('dss_bib_errors_fixed_step_4.txt', 'w', encoding='utf8') as f:
    for line in lines[True]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass

### Errors 3 - Biblical lines in different fonts step 5

> Some biblical lines are in Paleo-Hebrew. Here we delete the wrapper lines and add 'PH' to the end of the morph tag for the word that is in Paleo-Hebrew.

In [20]:
font = '-'

for line in lines[True]:
    if line.startswith('>'):
        font = '-'

    elif '(fl)' in line:
        font = 'PH'

    elif '(fy)' in line:
        font = '-'

    else:
        if font == 'PH':
            lines[True][lines[True].index(line)] = line + '\tPH'           
        else:
            lines[True][lines[True].index(line)] = line + '\t-'

In [ ]:
with open('dss_nonbib_errors_fixed_step_5.txt', 'w', encoding='utf8') as f:
    for line in lines[False]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass
        
with open('dss_bib_errors_fixed_step_5.txt', 'w', encoding='utf8') as f:
    for line in lines[True]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass

### Add Column for Hebrew/Aramaic step 6

In [21]:
for line in lines[False]:
    if not line.startwith('>'):
        if '%' in line:
            lines[False][lines[False].index(line)] = line + ' A'

        elif '@' in line:
            lines[False][lines[False].index(line)] = line + ' H'
            
        else:
            lines[False][lines[False].index(line)] = line + '\t-'

In [22]:
for line in lines[True]:
    if not line.startwith('>'):
        if '%' in line:
            lines[True][lines[True].index(line)] = line + ' A'

        elif '@' in line:
            lines[True][lines[True].index(line)] = line + ' H'
            
        else:
            lines[True][lines[True].index(line)] = line + '\t-'

In [ ]:
with open('dss_nonbib_errors_fixed_step_6.txt', 'w', encoding='utf8') as f:
    for line in lines[False]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass
        
with open('dss_bib_errors_fixed_step_6.txt', 'w', encoding='utf8') as f:
    for line in lines[True]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass

### Adjust and Create columns step 7

> Bib columns (11):
1. Book 
2. chapter
3. verse
4. Scroll
5. fragment
6. line
7. Transcription
8. Lexeme
9. morph tag
10. Bound (particles that are bound to the next word are marked with a 'B')
11. Script (PH= Paleohebrew)
12. Language (H = Hebrew, A = Aramaic)

>Non bib columns (9):
1. Scroll Name
2. Column
3. line
4. Transcription
5. Lexeme
6. morph tag
7. Bound (particles that are bound to the next word are marked with a 'B')
8. Interlinear (s1 and s2)
9. Script (PH = Paleohebrew, F0 and FT = not sure what these stand for, but kept them so more research can be done).
10. Language (H = Hebrew, A = Aramaic)


In [23]:
for line in lines[False]:
    updated_line1 = re.sub(' ', '\t', line)
    updated_line2 = re.sub('\:', '\t', updated_line1)
    updated_line3 = re.sub('\@', '\t', updated_line2)
    updated_line4 = re.sub('\%', '\t', updated_line3)

    
    lines[False][lines[False].index(line)] = updated_line4

In [24]:
for line in lines[True]:
    updated_line1 = re.sub('\t ', '\t', line)
    updated_line2 = re.sub(' \t ', '\t', updated_line1)
    updated_line3 = re.sub('\t\t', '\t', updated_line2)
    updated_line4 = re.sub('  ', '\t', updated_line3)
    updated_line5 = re.sub(' ', '\t', updated_line4)
    updated_line6 = re.sub('\:', '\t', updated_line5)
    updated_line7 = re.sub('\%\@', '\t', updated_line6)
    updated_line8 = re.sub('\@', '\t', updated_line7, 1)
    updated_line9 = re.sub('\%', '\t', updated_line8, 1)
    
    lines[True][lines[True].index(line)] = updated_line9

In [ ]:
with open('dss_nonbib_errors_fixed_step_7.txt', 'w', encoding='utf8') as f:
    for line in lines[False]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass
        
with open('dss_bib_errors_fixed_step_7.txt', 'w', encoding='utf8') as f:
    for line in lines[True]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass

### Fix specific errors

In [25]:
lines[True][lines[True].index('Is\t7\t22\t1Q8\t3\t3\tjm|\xa0\xa0a|h|\t\tjRmVaDh\tncfs\t-\t-')] = 'Is\t7\t22\t1Q8\t3\t3\tjm|\xa0\xa0a|h|\tjRmVaDh\tncfs\t-\t-'

lines[True][lines[True].index('Is	64	4	1Q8	27	30	owlM[	oøwlDMXncms	-	-	-	-')] = 'Is	64	4	1Q8	27	30	owlM[	oøwlDM\tncms	-	-'

lines[True][lines[True].index('Deut	20	7	4Q33	f37	1	ayC		aIyv	ncms	-	-')] = 'Deut	20	7	4Q33	f37	1	ayC	aIyv	ncms	-	-'

lines[True][lines[True].index('2Sam	3	26	4Q51	f61i+62	6	sy[rh	sIr∂h		np	-	-')] = '2Sam	3	26	4Q51	f61i+62	6	sy[rh	sIr∂h	np	-	-'

lines[True][lines[True].index('Judg	1	11	XJudges	f1	4	q]ryt		qIr√yÅt	np	-	-')] = 'Judg	1	11	XJudges	f1	4	q]ryt	qIr√yÅt	np	-	-'

ValueError: 'Is\t7\t22\t1Q8\t3\t3\tjm|\xa0\xa0a|h|\t\tjRmVaDh\tncfs\t-\t-' is not in list

In [ ]:
lines[True][lines[True].index('Deut	11	10	1Q4	f28	1	w	w◊	B	-	-	-')] = 'Deut	11	10	1Q4	f28	1	w	w◊	B	-	-'

lines[True][lines[True].index('Ps	44	8	1Q12	f1_4	6	w	w◊	B	-	-	-')] = 'Ps	44	8	1Q12	f1_4	6	w	w◊	B	-	-'

### Create new File with errors fixed

In [26]:
with open('dss_nonbib_errors_fixed.txt', 'w', encoding='utf8') as f:
    for line in lines[False]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass
        
with open('dss_bib_errors_fixed.txt', 'w', encoding='utf8') as f:
    for line in lines[True]:
        if not (line.startswith('>') or '' in line):
            f.write("%s\n" % line)
        else:
            pass

In [27]:
for line in lines[False]:
    if not (line.startswith('>') or '' in line):
        if line.count('\t') != 9:
            print(line)

CD	1	1	≥	-	-	-	-	-
CD	1	1	≤	-	-	-	-	-
CD	1	2	.	-	-	-	-	-
CD	1	2	.	-	-	-	-	-
CD	1	4	.	-	-	-	-	-
CD	1	5	.	-	-	-	-	-
CD	1	7	.	-	-	-	-	-
CD	1	8	.	-	-	-	-	-
CD	1	9	.	-	-	-	-	-
CD	1	10	.	-	-	-	-	-
CD	1	11	.	-	-	-	-	-
CD	1	11	≥	-	-	-	-	-
CD	1	11	≤	-	-	-	-	-
CD	1	13	.	-	-	-	-	-
CD	1	14	.	-	-	-	-	-
CD	1	18	.	-	-	-	-	-
CD	1	19	.	-	-	-	-	-
CD	1	21	.	-	-	-	-	-
CD	2	1	.	-	-	-	-	-
CD	2	2	≥	-	-	-	-	-
CD	2	2	≤	-	-	-	-	-
CD	2	3	.	-	-	-	-	-
CD	2	3	≥	-	-	-	-	-
CD	2	3	≤	-	-	-	-	-
CD	2	4	.	-	-	-	-	-
CD	2	5	.	-	-	-	-	-
CD	2	7	.	-	-	-	-	-
CD	2	8	.	-	-	-	-	-
CD	2	9	.	-	-	-	-	-
CD	2	10	.	-	-	-	-	-
CD	2	12	.	-	-	-	-	-
CD	2	12	≥	-	-	-	-	-
CD	2	12	≤	-	-	-	-	-
CD	2	13	.	-	-	-	-	-
CD	2	14	≥	-	-	-	-	-
CD	2	14	≤	-	-	-	-	-
CD	2	15	.	-	-	-	-	-
CD	2	17	.	-	-	-	-	-
CD	2	18	.	-	-	-	-	-
CD	2	19	.	-	-	-	-	-
CD	2	21	.	-	-	-	-	-
CD	3	1	≥	-	-	-	-	-
CD	3	1	≤	-	-	-	-	-
CD	3	1	.	-	-	-	-	-
CD	3	3	.	-	-	-	-	-
CD	3	4	.	-	-	-	-	-
CD	3	4	≥	-	-	-	-	-
CD	3	4	≤	-	-	-	-	-
CD	3	5	.	-	-	-	-	-
CD	3	6	.	-	-	-	-	-
CD	3	9	.	-	-	-	-	-
CD	3	10	.	

1QHa	4	40	.	-	-	-	-	-
1QHa	4	41	]	-	-	-	-	-
1QHa	4	41	[≥	-	-	-	-	-
1QHa	4	41	≤]	-	-	-	-	-
1QHa	4	41	[≥	-	-	B	-	-
1QHa	4	41	≤	-	-	-	-	-
1QHa	4	41	.	-	-	-	-	-
1QHa	5	13	]	-	-	-	-	-
1QHa	5	13	]	-	-	-	-	-
1QHa	5	14	]	-	-	-	-	-
1QHa	5	14	[	-	-	-	-	-
1QHa	5	14	]	-	-	-	-	-
1QHa	5	14	.	-	-	-	-	-
1QHa	5	15	]	-	-	-	-	-
1QHa	5	16	.	-	-	-	-	-
1QHa	5	17	]	-	-	-	-	-
1QHa	5	18	]	-	-	-	-	-
1QHa	5	18	.	-	-	-	-	-
1QHa	5	19	]	-	-	-	-	-
1QHa	5	19	[	-	-	-	-	-
1QHa	5	20	]	-	-	-	-	-
1QHa	5	20	[	-	-	-	-	-
1QHa	5	21	]	-	-	-	-	-
1QHa	5	21	[	-	-	-	-	-
1QHa	5	21	]	-	-	-	-	-
1QHa	5	21	.	-	-	-	-	-
1QHa	5	21	[	-	-	-	-	-
1QHa	5	22	]	-	-	-	-	-
1QHa	5	22	.	-	-	-	-	-
1QHa	5	22	[	-	-	-	-	-
1QHa	5	23	[	-	-	-	-	-
1QHa	5	24	]	-	-	-	-	-
1QHa	5	24	.	-	-	-	-	-
1QHa	5	24	≥	-	-	-	-	-
1QHa	5	24	≤	-	-	-	-	-
1QHa	5	27	.	-	-	-	-	-
1QHa	5	27	]	-	-	-	-	-
1QHa	5	29	.	-	-	-	-	-
1QHa	5	30	.	-	-	-	-	-
1QHa	5	30	.	-	-	-	-	-
1QHa	5	31	[	-	-	-	-	-
1QHa	5	31	.	-	-	-	-	-
1QHa	5	31	.	-	-	-	-	-
1QHa	5	32	.	-	-	-	-	-
1QHa	5	32	.	-	-	-	-	-
1QHa	5	

1Q20	6	24	[	-	-	-	-	-
1Q20	6	25	]	-	-	-	-	-
1Q20	6	25	]	-	-	-	-	-
1Q20	6	25	]	-	-	-	-	-
1Q20	6	25	[	-	-	-	-	-
1Q20	6	26	]	-	-	-	-	-
1Q20	6	26	[	-	-	-	-	-
1Q20	6	27	]	-	-	-	-	-
1Q20	6	27	]	-	-	-	-	-
1Q20	6	27	[	-	-	-	-	-
1Q20	6	27	.	-	-	-	-	-
1Q20	7	1	]	-	-	-	-	-
1Q20	7	2	]	-	-	-	-	-
1Q20	7	2	[	-	-	-	-	-
1Q20	7	2	.	-	-	-	-	-
1Q20	7	3	]	-	-	-	-	-
1Q20	7	3	]	-	-	-	-	-
1Q20	7	3	[	-	-	-	-	-
1Q20	7	3	]	-	-	-	-	-
1Q20	7	3	[	-	-	-	-	-
1Q20	7	4	]	-	-	-	-	-
1Q20	7	4	[	-	-	-	-	-
1Q20	7	5	]	-	-	-	-	-
1Q20	7	6	]	-	-	-	-	-
1Q20	7	6	[≥	-	-	-	-	-
1Q20	7	6	≤	-	-	-	-	-
1Q20	7	7	]	-	-	-	-	-
1Q20	7	7	[	-	-	-	-	-
1Q20	7	8	]	-	-	-	-	-
1Q20	7	8	[	-	-	-	-	-
1Q20	7	8	]	-	-	-	-	-
1Q20	7	9	]	-	-	-	-	-
1Q20	7	9	.	-	-	-	-	-
1Q20	7	9	≥	-	-	-	-	-
1Q20	7	9	≤	-	-	-	-	-
1Q20	7	10	]	-	-	-	-	-
1Q20	7	10	[	-	-	-	-	-
1Q20	7	11	]	-	-	-	-	-
1Q20	7	11	[	-	-	-	-	-
1Q20	7	12	]	-	-	-	-	-
1Q20	7	12	[	-	-	-	-	-
1Q20	7	13	]	-	-	-	-	-
1Q20	7	13	[	-	-	-	-	-
1Q20	7	14	]	-	-	-	-	-
1Q20	7	14	[	-	-	-	-	-
1Q20	7	15	]	-	-	-	-	-
1Q20	7	15	[

1Q36	f16	2	]	-	-	-	-	-
1Q36	f16	2	[	-	-	-	-	-
1Q36	f16	3	]	-	-	-	-	-
1Q36	f16	3	]	-	-	-	-	-
1Q36	f16	3	[	-	-	-	-	-
1Q36	f16	4	]	-	-	-	-	-
1Q36	f16	4	[	-	-	-	-	-
1Q36	f16	4	.	-	-	-	-	-
1Q36	f17	1	]	-	-	-	-	-
1Q36	f17	1	[	-	-	-	-	-
1Q36	f17	2	]	-	-	-	-	-
1Q36	f17	2	[	-	-	-	-	-
1Q36	f17	3	]	-	-	-	-	-
1Q36	f17	3	[	-	-	-	-	-
1Q36	f17	3	.	-	-	-	-	-
1Q36	f18	1	]	-	-	-	-	-
1Q36	f18	1	[	-	-	-	-	-
1Q36	f18	1	.	-	-	-	-	-
1Q36	f20	1	]	-	-	-	-	-
1Q36	f20	1	[	-	-	-	-	-
1Q36	f20	1	.	-	-	-	-	-
1Q36	f21	1	]	-	-	-	-	-
1Q36	f21	1	[	-	-	-	-	-
1Q36	f21	2	]	-	-	-	-	-
1Q36	f21	2	[	-	-	-	-	-
1Q36	f21	2	.	-	-	-	-	-
1Q36	f22	1	]	-	-	-	-	-
1Q36	f22	1	[	-	-	-	-	-
1Q36	f22	2	]	-	-	-	-	-
1Q36	f22	2	[	-	-	-	-	-
1Q36	f22	3	]	-	-	-	-	-
1Q36	f22	3	[	-	-	-	-	-
1Q36	f22	3	.	-	-	-	-	-
1Q36	f23	1	]	-	-	-	-	-
1Q36	f23	1	[	-	-	-	-	-
1Q36	f23	1	.	-	-	-	-	-
1Q36	f25i	4	]	-	-	-	-	-
1Q36	f25i	5	]	-	-	-	-	-
1Q36	f25i	5	.	-	-	-	-	-
1Q36	f25ii	1	[	-	-	-	-	-
1Q36	f25ii	2	[	-	-	-	-	-
1Q36	f25ii	3	[	-	-	-	-	-
1Q36	f25ii	4	]	-	-	-	-	-


4Q157	f1ii	10	.	-	-	-	-	-
4Q158	f1_2	1	]	-	-	-	-	-
4Q158	f1_2	1	[	-	-	-	-	-
4Q158	f1_2	2	]	-	-	-	-	-
4Q158	f1_2	2	[	-	-	-	-	-
4Q158	f1_2	3	]	-	-	-	-	-
4Q158	f1_2	3	.	-	-	-	-	-
4Q158	f1_2	3	[	-	-	-	-	-
4Q158	f1_2	3	.	-	-	-	-	-
4Q158	f1_2	3	[	-	-	-	-	-
4Q158	f1_2	4	]	-	-	-	-	-
4Q158	f1_2	4	[	-	-	-	-	-
4Q158	f1_2	5	]	-	-	-	-	-
4Q158	f1_2	5	.	-	-	-	-	-
4Q158	f1_2	5	[	-	-	-	-	-
4Q158	f1_2	6	]	-	-	-	-	-
4Q158	f1_2	6	.	-	-	-	-	-
4Q158	f1_2	6	.	-	-	-	-	-
4Q158	f1_2	6	[	-	-	-	-	-
4Q158	f1_2	7	]	-	-	-	-	-
4Q158	f1_2	7	.	-	-	-	-	-
4Q158	f1_2	7	.	-	-	-	-	-
4Q158	f1_2	7	[	-	-	-	-	-
4Q158	f1_2	8	.	-	-	-	-	-
4Q158	f1_2	8	[	-	-	-	-	-
4Q158	f1_2	9	.	-	-	-	-	-
4Q158	f1_2	9	[	-	-	-	-	-
4Q158	f1_2	10	.	-	-	-	-	-
4Q158	f1_2	10	[	-	-	-	-	-
4Q158	f1_2	11	.	-	-	-	-	-
4Q158	f1_2	11	[	-	-	-	-	-
4Q158	f1_2	12	.	-	-	-	-	-
4Q158	f1_2	12	[	-	-	-	-	-
4Q158	f1_2	13	.	-	-	-	-	-
4Q158	f1_2	13	[	-	-	-	-	-
4Q158	f1_2	14	.	-	-	-	-	-
4Q158	f1_2	14	[	-	-	-	-	-
4Q158	f1_2	15	]	-	-	-	-	-
4Q158	f1_2	15	.	-	-	-	-	-
4Q158	f1_2	1

...

4Q570	f7	1	[	-	-	-	-	-
4Q570	f7	2	]	-	-	-	-	-
4Q570	f7	2	[	-	-	-	-	-
4Q570	f7	3	]	-	-	-	-	-
4Q570	f7	3	[	-	-	-	-	-
4Q570	f7	4	]	-	-	-	-	-
4Q570	f7	4	[	-	-	-	-	-
4Q570	f7	5	]	-	-	-	-	-
4Q570	f7	5	[	-	-	-	-	-
4Q570	f7	5	.	-	-	-	-	-
4Q570	f8	1	]	-	-	-	-	-
4Q570	f8	1	[	-	-	-	-	-
4Q570	f8	2	]	-	-	-	-	-
4Q570	f8	2	[	-	-	-	-	-
4Q570	f8	3	]	-	-	-	-	-
4Q570	f8	3	[	-	-	-	-	-
4Q570	f8	4	]	-	-	-	-	-
4Q570	f8	4	[	-	-	-	-	-
4Q570	f8	5	]	-	-	-	-	-
4Q570	f8	5	[	-	-	-	-	-
4Q570	f8	5	.	-	-	-	-	-
4Q570	f9	1	]	-	-	-	-	-
4Q570	f9	1	[	-	-	-	-	-
4Q570	f9	2	]	-	-	-	-	-
4Q570	f9	2	[	-	-	-	-	-
4Q570	f9	3	]	-	-	-	-	-
4Q570	f9	3	[	-	-	-	-	-
4Q570	f9	4	]	-	-	-	-	-
4Q570	f9	4	]	-	-	-	-	-
4Q570	f9	4	[	-	-	-	-	-
4Q570	f9	4	.	-	-	-	-	-
4Q570	f10	1	]	-	-	-	-	-
4Q570	f10	1	[	-	-	-	-	-
4Q570	f10	2	]	-	-	-	-	-
4Q570	f10	2	[	-	-	-	-	-
4Q570	f10	3	]	-	-	-	-	-
4Q570	f10	3	[	-	-	-	-	-
4Q570	f10	3	.	-	-	-	-	-
4Q570	f11	1	]	-	-	-	-	-
4Q570	f11	1	[	-	-	-	-	-
4Q570	f11	2	]	-	-	-	-	-
4Q570	f11	2	[	-	-	-	-	-
4Q570	f11	3	]	-	-	-	-	-

6Q10	f4	5	[	-	-	B	-	-
6Q10	f4	5	.	-	-	-	-	-
6Q10	f6	1	]	-	-	-	-	-
6Q10	f6	1	[	-	-	-	-	-
6Q10	f6	2	]	-	-	-	-	-
6Q10	f6	2	[	-	-	B	-	-
6Q10	f6	2	.	-	-	-	-	-
6Q10	f7	1	]	-	-	-	-	-
6Q10	f7	1	[	-	-	-	-	-
6Q10	f7	1	[	-	-	B	-	-
6Q10	f7	1	.	-	-	-	-	-
6Q10	f8	1	]	-	-	-	-	-
6Q10	f8	1	[	-	-	-	-	-
6Q10	f8	2	]	-	-	-	-	-
6Q10	f8	2	[	-	-	B	-	-
6Q10	f8	2	.	-	-	-	-	-
6Q10	f9	1	]	-	-	-	-	-
6Q10	f9	1	[	-	-	B	-	-
6Q10	f9	1	.	-	-	-	-	-
6Q10	f10	1	]	-	-	-	-	-
6Q10	f10	1	[	-	-	-	-	-
6Q10	f10	1	[	-	-	B	-	-
6Q10	f10	1	.	-	-	-	-	-
6Q10	f11	1	]	-	-	-	-	-
6Q10	f11	1	[	-	-	B	-	-
6Q10	f11	1	.	-	-	-	-	-
6Q10	f12	1	[	-	-	-	-	-
6Q10	f12	2	]	-	-	-	-	-
6Q10	f12	2	[	-	-	B	-	-
6Q10	f12	2	.	-	-	-	-	-
6Q10	f13	1	]	-	-	-	-	-
6Q10	f13	1	]	-	-	-	-	-
6Q10	f13	1	[	-	-	-	-	-
6Q10	f13	2	]	-	-	-	-	-
6Q10	f13	2	[	-	-	-	-	-
6Q10	f13	2	[	-	-	B	-	-
6Q10	f13	2	.	-	-	-	-	-
6Q10	f14	1	[	-	-	-	-	-
6Q10	f14	2	[	-	-	B	-	-
6Q10	f14	2	.	-	-	-	-	-
6Q10	f15	1	]	-	-	-	-	-
6Q10	f15	1	[	-	-	-	-	-
6Q10	f15	2	]	-	-	-	-	-
6Q10	f15	2	[	-	-	-	-	-
6Q10	f1

11Q18	f8	2	[	-	-	-	-	-
11Q18	f8	3	]	-	-	-	-	-
11Q18	f8	3	[	-	-	-	-	-
11Q18	f8	4	]	-	-	-	-	-
11Q18	f8	4	[	-	-	-	-	-
11Q18	f8	5	]	-	-	-	-	-
11Q18	f8	5	[	-	-	-	-	-
11Q18	f8	5	.	-	-	-	-	-
11Q18	f9	1	]	-	-	-	-	-
11Q18	f9	1	[	-	-	-	-	-
11Q18	f9	1	[	-	-	-	-	-
11Q18	f9	2	]	-	-	-	-	-
11Q18	f9	2	[	-	-	-	-	-
11Q18	f9	3	]	-	-	-	-	-
11Q18	f9	3	]	-	-	-	-	-
11Q18	f9	3	[	-	-	-	-	-
11Q18	f9	4	]	-	-	-	-	-
11Q18	f9	4	[	-	-	-	-	-
11Q18	f9	5	]	-	-	-	-	-
11Q18	f9	5	]	-	-	-	-	-
11Q18	f9	5	[	-	-	-	-	-
11Q18	f9	6	]	-	-	-	-	-
11Q18	f9	6	[	-	-	-	-	-
11Q18	f9	6	.	-	-	-	-	-
11Q18	f10i	1	]	-	-	-	-	-
11Q18	f10i	2	]	-	-	-	-	-
11Q18	f10i	3	]	-	-	-	-	-
11Q18	f10i	4	]	-	-	-	-	-
11Q18	f10i	4	[≥	-	-	-	-	-
11Q18	f10i	4	≤	-	-	-	-	-
11Q18	f10i	5	]	-	-	-	-	-
11Q18	f10i	6	]	-	-	-	-	-
11Q18	f10i	7	]	-	-	-	-	-
11Q18	f10i	8	]	-	-	-	-	-
11Q18	f10i	8	[	-	-	-	-	-
11Q18	f10i	8	.	-	-	-	-	-
11Q18	f10ii	1	[	-	-	-	-	-
11Q18	f10ii	2	[	-	-	-	-	-
11Q18	f10ii	3	[	-	-	-	-	-
11Q18	f10ii	4	[	-	-	-	-	-
11Q18	f10ii	5	[	-	-	-	-	-
11Q18	f10ii	6	[	-

11Q23	f3	2	[	-	-	-	-	-
11Q23	f3	3	]	-	-	-	-	-
11Q23	f3	3	[	-	-	-	-	-
11Q23	f3	4	]	-	-	-	-	-
11Q23	f3	4	[	-	-	-	-	-
11Q23	f3	4	.	-	-	-	-	-
11Q25	f1	1	[	-	-	-	-	-
11Q25	f1	2	[	-	-	-	-	-
11Q25	f1	3	]	-	-	-	-	-
11Q25	f1	3	[	-	-	-	-	-
11Q25	f1	3	.	-	-	-	-	-
11Q25	f2	1	[	-	-	-	-	-
11Q25	f2	1	.	-	-	-	-	-
11Q25	f3	1	[	-	-	-	-	-
11Q25	f3	2	]	-	-	-	-	-
11Q25	f3	2	[	-	-	-	-	-
11Q25	f3	2	.	-	-	-	-	-
11Q25	f4	1	]	-	-	-	-	-
11Q25	f4	1	[	-	-	-	-	-
11Q25	f4	2	]	-	-	-	-	-
11Q25	f4	2	[	-	-	-	-	-
11Q25	f4	3	]	-	-	-	-	-
11Q25	f4	3	[	-	-	-	-	-
11Q25	f4	4	]	-	-	-	-	-
11Q25	f4	4	[	-	-	-	-	-
11Q25	f4	4	.	-	-	-	-	-
11Q25	f5	1	]	-	-	-	-	-
11Q25	f5	1	]	-	-	-	-	-
11Q25	f5	1	[	-	-	-	-	-
11Q25	f5	1	.	-	-	-	-	-
11Q25	f6	1	]	-	-	-	-	-
11Q25	f6	1	[	-	-	-	-	-
11Q25	f6	2	]	-	-	-	-	-
11Q25	f6	2	[	-	-	-	-	-
11Q25	f6	2	.	-	-	-	-	-
11Q25	f7	1	]	-	-	-	-	-
11Q25	f7	1	[	-	-	-	-	-
11Q25	f7	1	.	-	-	-	-	-
11Q25	f8	1	]	-	-	-	-	-
11Q25	f8	1	[	-	-	-	-	-
11Q25	f8	2	]	-	-	-	-	-
11Q25	f8	2	[	-	-	-	-	-
11Q25	f8	2	.	-	-	-	-	-
11Q26	f1	1	

PAM43685	f14	2	]	-	-	-	-	-
PAM43685	f14	2	[	-	-	-	-	-
PAM43685	f14	2	.	-	-	-	-	-
PAM43685	f21	1	[	-	-	-	-	-
PAM43685	f21	2	[	-	-	-	-	-
PAM43685	f22	1	]	-	-	-	-	-
PAM43685	f22	2	]	-	-	-	-	-
PAM43685	f22	3	]	-	-	-	-	-
PAM43685	f22	3	.	-	-	-	-	-
PAM43685	f23	1	]	-	-	-	-	-
PAM43685	f23	1	[	-	-	-	-	-
PAM43685	f23	2	]	-	-	-	-	-
PAM43685	f23	2	[	-	-	-	-	-
PAM43685	f23	2	.	-	-	-	-	-
PAM43685	f24	1	]	-	-	-	-	-
PAM43685	f24	1	[	-	-	-	-	-
PAM43685	f24	1	[	-	-	-	-	-
PAM43685	f24	2	]	-	-	-	-	-
PAM43685	f24	2	[	-	-	-	-	-
PAM43685	f24	2	.	-	-	-	-	-
PAM43685	f31	1	]	-	-	-	-	-
PAM43685	f31	1	≥	-	-	-	-	-
PAM43685	f31	1	≤]	-	-	-	-	-
PAM43685	f31	1	[	-	-	-	-	-
PAM43685	f31	1	.	-	-	-	-	-
PAM43685	f40	1	]	-	-	-	-	-
PAM43685	f40	1	[	-	-	-	-	-
PAM43685	f40	1	.	-	-	-	-	-
PAM43685	f48	1	]	-	-	-	-	-
PAM43685	f48	1	[	-	-	-	-	-
PAM43685	f48	2	]	-	-	-	-	-
PAM43685	f48	2	[	-	-	-	-	-
PAM43685	f48	2	.	-	-	-	-	-
PAM43685	f49	1	]	-	-	-	-	-
PAM43685	f49	1	[	-	-	-	-	-
PAM43685	f49	2	]	-	-	-	-	-
PAM43685	f49	2	.	-	-	-	-	-


In [28]:
for line in lines[True]:
    if not (line.startswith('>') or '' in line):
        if line.count('\t') != 11:
            print(line)

Gen	1	18	1Q1	f1	1	.	-	-	-	-
Gen	1	19	1Q1	f1	1	.	-	-	-	-
Gen	1	20	1Q1	f1	1	/	-	-	-	-
Gen	1	20	1Q1	f1	2	.	-	-	-	-
Gen	1	20	1Q1	f1	2	[	-	-	-	-
Gen	1	20	1Q1	f1	2	/	-	-	-	-
Gen	1	21	1Q1	f1	3	.	-	-	-	-
Gen	1	21	1Q1	f1	3	/	-	-	-	-
Gen	3	11	1Q1	f2	1	/	-	-	-	-
Gen	3	11	1Q1	f2	2	.	-	-	-	-
Gen	3	12	1Q1	f2	2	.	-	-	-	-
Gen	3	13	1Q1	f2	2	/	-	-	-	-
Gen	3	13	1Q1	f2	3	.	-	-	-	-
Gen	3	14	1Q1	f2	3	/	-	-	-	-
Gen	3	14	1Q1	f2	4	/	-	-	-	-
Gen	3	14	1Q1	f2	5	.	-	-	-	-
Gen	3	14	1Q1	f2	5	[	-	-	-	-
Gen	3	14	1Q1	f2	5	/	-	-	-	-
Gen	22	13	1Q1	f3	1	.	-	-	-	-
Gen	22	13	1Q1	f3	1	[	-	-	-	-
Gen	22	13	1Q1	f3	1	/	-	-	-	-
Gen	22	14	1Q1	f3	2	/	-	-	-	-
Gen	22	14	1Q1	f3	3	.	-	-	-	-
Gen	22	15	1Q1	f3	3	.	-	-	-	-
Gen	22	15	1Q1	f3	3	[	-	-	-	-
Gen	22	15	1Q1	f3	3	/	-	-	-	-
Gen	23	17	1Q1	f4	1	]	-	-	-	-
Gen	23	17	1Q1	f4	1	/	-	-	-	-
Gen	23	17	1Q1	f4	2	/	-	-	-	-
Gen	23	17	1Q1	f4	3	.	-	-	-	-
Gen	23	18	1Q1	f4	3	/	-	-	-	-
Gen	23	18	1Q1	f4	4	.	-	-	-	-
Gen	23	19	1Q1	f4	4	/	-	-	-	-
Gen	23	19	1Q1	f4	5	.	-	-	-	-
Gen	23	19	1Q1	f4	5	[	-	-	-	-
Gen

Is	19	1	1QIsaa	15	5	.	-	-	-	-
Is	19	2	1QIsaa	15	5	/	-	-	-	-
Is	19	2	1QIsaa	15	6	.	-	-	-	-
Is	19	3	1QIsaa	15	6	/	-	-	-	-
Is	19	3	1QIsaa	15	7	/	-	-	-	-
Is	19	3	1QIsaa	15	8	.	-	-	-	-
Is	19	4	1QIsaa	15	8	/	-	-	-	-
Is	19	4	1QIsaa	15	9	.	-	-	-	-
Is	19	5	1QIsaa	15	9	.	-	-	-	-
Is	19	5	1QIsaa	15	9	/	-	-	-	-
Is	19	6	1QIsaa	15	10	.	-	-	-	-
Is	19	7	1QIsaa	15	10	/	-	-	-	-
Is	19	7	1QIsaa	15	11	.	-	-	-	-
Is	19	8	1QIsaa	15	11	/	-	-	-	-
Is	19	8	1QIsaa	15	12	.	-	-	-	-
Is	19	9	1QIsaa	15	12	/	-	-	-	-
Is	19	9	1QIsaa	15	13	.	-	-	-	-
Is	19	10	1QIsaa	15	13	/	-	-	-	-
Is	19	10	1QIsaa	15	14	.	-	-	-	-
Is	19	11	1QIsaa	15	14	/	-	-	-	-
Is	19	11	1QIsaa	15	15	.	-	-	-	-
Is	19	12	1QIsaa	15	15	/	-	-	-	-
Is	19	12	1QIsaa	15	16	.	-	-	-	-
Is	19	13	1QIsaa	15	16	/	-	-	-	-
Is	19	13	1QIsaa	15	17	.	-	-	-	-
Is	19	14	1QIsaa	15	17	/	-	-	-	-
Is	19	14	1QIsaa	15	18	/	-	-	-	-
Is	19	14	1QIsaa	15	19	.	-	-	-	-
Is	19	15	1QIsaa	15	19	/	-	-	-	-
Is	19	15	1QIsaa	15	20	.	-	-	-	-
Is	19	15	1QIsaa	15	20	≥	-	-	-	-
Is	19	15	1QIsaa	15	20	≤	-	-	-	-
Is	

Is	54	1	1QIsaa	44	24	.	-	-	-	-
Is	54	2	1QIsaa	44	24	/	-	-	-	-
Is	54	2	1QIsaa	44	25	/	-	-	-	-
Is	54	2	1QIsaa	44	26	.	-	-	-	-
Is	54	3	1QIsaa	44	26	/	-	-	-	-
Is	54	3	1QIsaa	44	27	.	-	-	-	-
Is	54	4	1QIsaa	44	27	/	-	-	-	-
Is	54	4	1QIsaa	44	28	/	-	-	-	-
Is	54	4	1QIsaa	45	1	.	-	-	-	-
Is	54	5	1QIsaa	45	1	/	-	-	-	-
Is	54	5	1QIsaa	45	2	.	-	-	-	-
Is	54	6	1QIsaa	45	2	/	-	-	-	-
Is	54	6	1QIsaa	45	3	.	-	-	-	-
Is	54	6	1QIsaa	45	3	/	-	-	-	-
Is	54	7	1QIsaa	45	4	.	-	-	-	-
Is	54	8	1QIsaa	45	4	/	-	-	-	-
Is	54	8	1QIsaa	45	5	/	-	-	-	-
Is	54	8	1QIsaa	45	6	.	-	-	-	-
Is	54	9	1QIsaa	45	6	/	-	-	-	-
Is	54	9	1QIsaa	45	7	.	-	-	-	-
Is	54	10	1QIsaa	45	7	/	-	-	-	-
Is	54	10	1QIsaa	45	8	/	-	-	-	-
Is	54	10	1QIsaa	45	9	.	-	-	-	-
Is	54	10	1QIsaa	45	9	≥	-	-	-	-
Is	54	10	1QIsaa	45	9	≤	-	-	-	-
Is	54	10	1QIsaa	45	9	/	-	-	-	-
Is	54	11	1QIsaa	45	10	/	-	-	-	-
Is	54	11	1QIsaa	45	11	.	-	-	-	-
Is	54	12	1QIsaa	45	11	/	-	-	-	-
Is	54	12	1QIsaa	45	12	.	-	-	-	-
Is	54	13	1QIsaa	45	12	.	-	-	-	-
Is	54	13	1QIsaa	45	12	/	-	-	-	-
Is	54	14	1QIsa

Ps	119	79	1Q10	f11	3	]	-	-	-	-
Ps	119	79	1Q10	f11	3	[	-	-	-	-
Ps	119	79	1Q10	f11	3	.	-	-	-	-
Ps	119	79	1Q10	f11	3	/	-	-	-	-
Ps	119	80	1Q10	f11	4	]	-	-	-	-
Ps	119	80	1Q10	f11	4	[	-	-	-	-
Ps	119	80	1Q10	f11	4	.	-	-	-	-
Ps	119	80	1Q10	f11	4	/	-	-	-	-
1Q10	f12	1	1Q10	f12	1	]	-	-	-	-
1Q10	f12	1	1Q10	f12	1	[≥	-	-	-	-
1Q10	f12	1	1Q10	f12	1	≤]	-	-	-	-
1Q10	f12	1	1Q10	f12	1	[	-	-	-	-
1Q10	f12	1	1Q10	f12	1	/	-	-	-	-
1Q10	f12	2	1Q10	f12	2	]	-	-	-	-
1Q10	f12	2	1Q10	f12	2	≥	-	-	-	-
1Q10	f12	2	1Q10	f12	2	≤	-	-	-	-
1Q10	f12	2	1Q10	f12	2	[	-	-	-	-
1Q10	f12	2	1Q10	f12	2	.	-	-	-	-
1Q10	f12	2	1Q10	f12	2	/	-	-	-	-
1Q10	f15	1	1Q10	f15	1	]	-	-	-	-
1Q10	f15	1	1Q10	f15	1	[	-	-	-	-
1Q10	f15	1	1Q10	f15	1	/	-	-	-	-
1Q10	f15	2	1Q10	f15	2	]	-	-	-	-
1Q10	f15	2	1Q10	f15	2	[	-	-	-	-
1Q10	f15	2	1Q10	f15	2	/	-	-	-	-
1Q10	f15	3	1Q10	f15	3	]	-	-	-	-
1Q10	f15	3	1Q10	f15	3	[	-	-	-	-
1Q10	f15	3	1Q10	f15	3	.	-	-	-	-
1Q10	f15	3	1Q10	f15	3	/	-	-	-	-
1Q10	f16	1	1Q10	f16	1	]	-	-	-	-
1Q10	f16	1	1Q10	f16	1	[	-	-	-	-
1Q10	f16	1	1Q1

Gen	40	19	4Q3	f1ii	3	.	-	-	-	-
Gen	40	20	4Q3	f1ii	3	/	-	-	-	-
Gen	40	20	4Q3	f1ii	4	/	-	-	-	-
Gen	40	20	4Q3	f1ii	5	.	-	-	-	-
Gen	40	21	4Q3	f1ii	5	/	-	-	-	-
Gen	40	21	4Q3	f1ii	6	.	-	-	-	-
Gen	40	22	4Q3	f1ii	6	.	-	-	-	-
Gen	40	23	4Q3	f1ii	6	/	-	-	-	-
Gen	40	23	4Q3	f1ii	7	.	-	-	-	-
Gen	41	1	4Q3	f1ii	7	/	-	-	-	-
Gen	41	1	4Q3	f1ii	8	.	-	-	-	-
Gen	41	2	4Q3	f1ii	8	/	-	-	-	-
Gen	41	2	4Q3	f1ii	9	.	-	-	-	-
Gen	41	3	4Q3	f1ii	9	/	-	-	-	-
Gen	41	3	4Q3	f1ii	10	.	-	-	-	-
Gen	41	3	4Q3	f1ii	10	≥	-	-	-	-
Gen	41	3	4Q3	f1ii	10	≤	-	-	-	-
Gen	41	4	4Q3	f1ii	10	/	-	-	-	-
Gen	41	4	4Q3	f1ii	11	≥	-	-	-	-
Gen	41	4	4Q3	f1ii	11	≤	-	-	-	-
Gen	41	4	4Q3	f1ii	11	/	-	-	-	-
Gen	41	4	4Q3	f1ii	12	.	-	-	-	-
Gen	41	5	4Q3	f1ii	12	≥	-	-	-	-
Gen	41	5	4Q3	f1ii	12	≤	-	-	-	-
Gen	41	5	4Q3	f1ii	12	/	-	-	-	-
Gen	41	5	4Q3	f1ii	13	.	-	-	-	-
Gen	41	6	4Q3	f1ii	13	.	-	-	-	-
Gen	41	7	4Q3	f1ii	13	/	-	-	-	-
Gen	41	7	4Q3	f1ii	14	/	-	-	-	-
Gen	41	7	4Q3	f1ii	15	.	-	-	-	-
Gen	41	8	4Q3	f1ii	15	/	-	-	-	-
Gen	41	8	4Q3	f1ii	16	.	-	-	-	-
Gen	41	9	4Q3	

...

Ps	107	39	4Q88	4	20	.	-	-	-	-
Ps	107	40	4Q88	4	20	/	-	-	-	-
Ps	107	40	4Q88	4	21	.	-	-	-	-
Ps	107	41	4Q88	4	21	/	-	-	-	-
Ps	107	41	4Q88	4	22	[	-	-	-	-
Ps	107	41	4Q88	4	22	/	-	-	-	-
Ps	107	41	4Q88	4	23	.	-	-	-	-
Ps	107	41	4Q88	4	23	/	-	-	-	-
Ps	107	42	4Q88	4	24	/	-	-	-	-
Ps	107	42	4Q88	4	25	[	-	-	-	-
Ps	107	42	4Q88	4	25	.	-	-	-	-
Ps	107	42	4Q88	4	25	/	-	-	-	-
Ps	109	4	4Q88	6	1	.	-	-	-	-
Ps	109	5	4Q88	6	1	/	-	-	-	-
Ps	109	5	4Q88	6	2	.	-	-	-	-
Ps	109	5	4Q88	6	2	/	-	-	-	-
Ps	109	6	4Q88	6	3	/	-	-	-	-
Ps	109	6	4Q88	6	4	.	-	-	-	-
Ps	109	7	4Q88	6	4	[	-	-	-	-
Ps	109	7	4Q88	6	4	.	-	-	-	-
Ps	109	7	4Q88	6	4	/	-	-	-	-
Ps	109	24	4Q88	7	2	]	-	-	-	-
Ps	109	24	4Q88	7	2	/	-	-	-	-
Ps	109	24	4Q88	7	3	.	-	-	-	-
Ps	109	24	4Q88	7	3	/	-	-	-	-
Ps	109	25	4Q88	7	4	/	-	-	-	-
Ps	109	25	4Q88	7	5	.	-	-	-	-
Ps	109	26	4Q88	7	5	/	-	-	-	-
Ps	109	26	4Q88	7	6	.	-	-	-	-
Ps	109	27	4Q88	7	6	.	-	-	-	-
Ps	109	27	4Q88	7	6	/	-	-	-	-
Ps	109	28	4Q88	7	7	/	-	-	-	-
Ps	109	28	4Q88	7	8	.	-	-	-	-
Ps	109	28	4Q88	7	8	/	-	-	-	-
4Q88	f3	1	4

Ezra	4	11	4Q117	f2	4	/	-	-	-	-
Ezra	5	17	4Q117	f3	1	]	-	-	-	-
Ezra	5	17	4Q117	f3	1	/	-	-	-	-
Ezra	5	17	4Q117	f3	2	.	-	-	-	-
Ezra	5	17	4Q117	f3	2	/	-	-	-	-
Ezra	6	1	4Q117	f3	3	.	-	-	-	-
Ezra	6	2	4Q117	f3	3	/	-	-	-	-
Ezra	6	2	4Q117	f3	4	.	-	-	-	-
Ezra	6	3	4Q117	f3	4	/	-	-	-	-
Ezra	6	3	4Q117	f3	5	/	-	-	-	-
Ezra	6	3	4Q117	f3	6	.	-	-	-	-
Ezra	6	4	4Q117	f3	6	/	-	-	-	-
Ezra	6	4	4Q117	f3	7	.	-	-	-	-
Ezra	6	5	4Q117	f3	7	/	-	-	-	-
Ezra	6	5	4Q117	f3	8	/	-	-	-	-
Ezra	6	5	4Q117	f3	9	.	-	-	-	-
Ezra	6	5	4Q117	f3	9	≥	-	-	-	-
Ezra	6	5	4Q117	f3	9	≤	-	-	-	-
Ezra	6	6	4Q117	f3	9	[	-	-	-	-
Ezra	6	6	4Q117	f3	9	.	-	-	-	-
Ezra	6	6	4Q117	f3	9	/	-	-	-	-
4Q118	f1i	4	4Q118	f1i	4	]	-	-	-	-
4Q118	f1i	4	4Q118	f1i	4	/	-	-	-	-
4Q118	f1i	5	4Q118	f1i	5	]	-	-	-	-
4Q118	f1i	5	4Q118	f1i	5	/	-	-	-	-
4Q118	f1i	6	4Q118	f1i	6	]	-	-	-	-
4Q118	f1i	6	4Q118	f1i	6	.	-	-	-	-
4Q118	f1i	6	4Q118	f1i	6	/	-	-	-	-
2Chr	28	27	4Q118	f1ii	1	]	-	-	-	-
2Chr	28	27	4Q118	f1ii	1	/	-	-	-	-
2Chr	28	27	4Q118	f1ii	2	.	-	-	-	-
2Chr	29	1	4Q118	f1ii	2	/	

6Q4	f59	1	6Q4	f59	1	]	-	-	-	-
6Q4	f59	1	6Q4	f59	1	[	-	-	-	-
6Q4	f59	1	6Q4	f59	1	.	-	-	-	-
6Q4	f59	1	6Q4	f59	1	/	-	-	-	-
6Q4	f62	1	6Q4	f62	1	]	-	-	-	-
6Q4	f62	1	6Q4	f62	1	[	-	-	-	-
6Q4	f62	1	6Q4	f62	1	[	-	-	-	-
6Q4	f62	1	6Q4	f62	1	.	-	-	-	-
6Q4	f62	1	6Q4	f62	1	/	-	-	-	-
6Q4	f63	1	6Q4	f63	1	]	-	-	-	-
6Q4	f63	1	6Q4	f63	1	[	-	-	-	-
6Q4	f63	1	6Q4	f63	1	[	-	-	-	-
6Q4	f63	1	6Q4	f63	1	.	-	-	-	-
6Q4	f63	1	6Q4	f63	1	/	-	-	-	-
6Q4	f64	1	6Q4	f64	1	]	-	-	-	-
6Q4	f64	1	6Q4	f64	1	[	-	-	-	-
6Q4	f64	1	6Q4	f64	1	/	-	-	-	-
6Q4	f64	2	6Q4	f64	2	]	-	-	-	-
6Q4	f64	2	6Q4	f64	2	[	-	-	-	-
6Q4	f64	2	6Q4	f64	2	.	-	-	-	-
6Q4	f64	2	6Q4	f64	2	/	-	-	-	-
6Q4	f65	1	6Q4	f65	1	]	-	-	-	-
6Q4	f65	1	6Q4	f65	1	[	-	-	-	-
6Q4	f65	1	6Q4	f65	1	.	-	-	-	-
6Q4	f65	1	6Q4	f65	1	/	-	-	-	-
6Q4	f66	1	6Q4	f66	1	]	-	-	-	-
6Q4	f66	1	6Q4	f66	1	[	-	-	-	-
6Q4	f66	1	6Q4	f66	1	/	-	-	-	-
6Q4	f66	2	6Q4	f66	2	]	-	-	-	-
6Q4	f66	2	6Q4	f66	2	]	-	-	-	-
6Q4	f66	2	6Q4	f66	2	[	-	-	-	-
6Q4	f66	2	6Q4	f66	2	.	-	-	-	-
6Q4	f66	2	6Q4	f66	2	/	-	-	-	-
6Q4	f67	1	

Ps	119	91	11Q5	10	10	/	-	-	-	-
Ps	119	92	11Q5	10	11	.	-	-	-	-
Ps	119	92	11Q5	10	11	/	-	-	-	-
Ps	119	93	11Q5	10	12	.	-	-	-	-
Ps	119	93	11Q5	10	12	/	-	-	-	-
Ps	119	94	11Q5	10	13	.	-	-	-	-
Ps	119	94	11Q5	10	13	/	-	-	-	-
Ps	119	95	11Q5	10	14	.	-	-	-	-
Ps	119	95	11Q5	10	14	/	-	-	-	-
Ps	119	96	11Q5	10	15	.	-	-	-	-
Ps	119	96	11Q5	10	15	/	-	-	-	-
Ps	119	105	11Q5	11	1	.	-	-	-	-
Ps	119	105	11Q5	11	1	/	-	-	-	-
Ps	119	106	11Q5	11	2	.	-	-	-	-
Ps	119	106	11Q5	11	2	/	-	-	-	-
Ps	119	107	11Q5	11	3	.	-	-	-	-
Ps	119	107	11Q5	11	3	/	-	-	-	-
Ps	119	108	11Q5	11	4	.	-	-	-	-
Ps	119	108	11Q5	11	4	/	-	-	-	-
Ps	119	109	11Q5	11	5	.	-	-	-	-
Ps	119	109	11Q5	11	5	/	-	-	-	-
Ps	119	110	11Q5	11	6	.	-	-	-	-
Ps	119	110	11Q5	11	6	/	-	-	-	-
Ps	119	111	11Q5	11	7	.	-	-	-	-
Ps	119	111	11Q5	11	7	/	-	-	-	-
Ps	119	112	11Q5	11	8	.	-	-	-	-
Ps	119	112	11Q5	11	8	/	-	-	-	-
Ps	119	113	11Q5	11	9	.	-	-	-	-
Ps	119	113	11Q5	11	9	/	-	-	-	-
Ps	119	114	11Q5	11	10	.	-	-	-	-
Ps	119	114	11Q5	11	10	/	-	-	-	-
Ps	119	115	11Q5	11	11	.	-	-	-	-
Ps	11

Zeph	3	8	Mur88	21	3	.	-	-	-	-
Zeph	3	9	Mur88	21	3	/	-	-	-	-
Zeph	3	9	Mur88	21	4	.	-	-	-	-
Zeph	3	10	Mur88	21	4	/	-	-	-	-
Zeph	3	10	Mur88	21	5	.	-	-	-	-
Zeph	3	11	Mur88	21	5	/	-	-	-	-
Zeph	3	11	Mur88	21	6	.	-	-	-	-
Zeph	3	11	Mur88	21	6	/	-	-	-	-
Zeph	3	12	Mur88	21	7	.	-	-	-	-
Zeph	3	13	Mur88	21	7	/	-	-	-	-
Zeph	3	13	Mur88	21	8	/	-	-	-	-
Zeph	3	13	Mur88	21	9	.	-	-	-	-
Zeph	3	13	Mur88	21	9	≥	-	-	-	-
Zeph	3	13	Mur88	21	9	≤	-	-	-	-
Zeph	3	13	Mur88	21	9	/	-	-	-	-
Zeph	3	13	Mur88	21	10	≥	-	-	-	-
Zeph	3	13	Mur88	21	10	≤	-	-	-	-
Zeph	3	14	Mur88	21	10	/	-	-	-	-
Zeph	3	14	Mur88	21	11	.	-	-	-	-
Zeph	3	15	Mur88	21	11	/	-	-	-	-
Zeph	3	15	Mur88	21	12	.	-	-	-	-
Zeph	3	16	Mur88	21	12	/	-	-	-	-
Zeph	3	16	Mur88	21	13	.	-	-	-	-
Zeph	3	17	Mur88	21	13	/	-	-	-	-
Zeph	3	17	Mur88	21	14	.	-	-	-	-
Zeph	3	18	Mur88	21	14	/	-	-	-	-
Zeph	3	18	Mur88	21	15	.	-	-	-	-
Zeph	3	19	Mur88	21	15	/	-	-	-	-
Zeph	3	19	Mur88	21	16	/	-	-	-	-
Zeph	3	19	Mur88	21	17	.	-	-	-	-
Zeph	3	20	Mur88	21	17	/	-	-	-	-
Zeph	3	20	Mur88	21	18	/	-	

### tests

In [ ]:
lines[True][lines[True].index(Is	7	22	1Q8	3	3	jm|  a|h|	jRmVaDh	ncfs	-	-)] = line + '\tPH'

In [ ]:
lines[True].index('Is 7:22	1Q8 3:3	jm|  a|h| 	jRmVaDh@ncfs	31')

In [ ]:
lines[True][32131]

In [ ]:
# non biblical - fixed

1QSa 1:8,6.1 ÊÊ

# biblical errors

# four extra columns intead of three, original has no morph tag - fixed
Deut	11	10	1Q4	f28	1	w	w◊	B	-	-	-
Deut 11:10	1Q4 f28:1	w	w◊	14729.7

# double space after vertical line and two tabs - fixed
Is	7	22	1Q8	3	3	jm|  a|h|		jRmVaDh	ncfs	-	-
Is 7:22	1Q8 3:3	jm|  a|h| 	jRmVaDh@ncfs	31

# four extra columns instead of three - X should be @ - fixed
Is	64	4	1Q8	27	30	owlM[	oøwlDMXncms	-	-	-	-
Is 64:4	1Q8 27:30	owlM[	oøwlDMXncms	25242

# four extra columns intead of three, original has no morph tag - fixed
Ps	44	8	1Q12	f1_4	6	w	w◊	B	-	-	-
Ps 44:8	1Q12 f1_4:6	w	w◊	401.5

# two tabs in a row, original has space + tab - fixed
Deut	20	7	4Q33	f37	1	ayC		aIyv	ncms	-	-
Deut 20:7	4Q33 f37:1	ayC 	aIyv@ncms	15429

# two tabs in a row, original has two spaces -fixed
2Sam	3	26	4Q51	f61i+62	6	sy[rh	sIr∂h		np	-	-
2Sam 3:26	4Q51 f61i+62:6	sy[rh	sIr∂h  @np	5764


# two tabs, original has space + tab
Judg	1	11	XJudges	f1	4	q]ryt		qIr√yÅt	np	-	-
Judg 1:11	XJudges f1:4	q]ryt 	qIr√yÅt@np	1221


In [ ]:
string = 'CD	1	1	w	w◊	Pc	B	-	-'

string.count('\t')

In [ ]:
Eccl	1	15	4Q110	f1_3	10	l	lV	Pp	0	B	-
Eccl 1:15	4Q110 f1_3:10	l	lV@Pp@0	409.5
        
Is	7	22	1Q8	3	3	jm|  a|h|		jRmVaDh	ncfs	-	-
Is 7:22	1Q8 3:3	jm|  a|h| 	jRmVaDh@ncfs	31




In [ ]:
list = ['>4Q559 f12:1',
'4Q559 f12:1 ] - - - -',
'4Q559 f12:1 -- \%0 B - -',
'(fl) -',
'4Q559 f12:1 [D|] 02%uc000 - - PH',
'(fy) -',
'4Q559 f12:1 -- \%0 - - -']

for line in list:
    if not ('\@' in line or '%' in line):
    # if not ('4' in line or 'fl' in line):
        list[list.index(line)] = line + ' T'
print(list)

In [ ]:
string = 'CD	5	3	}}np\\{{	p\\@vnPmsa	-	-	-'

s_update = re.sub('\@', '\t', string)

s_update

In [ ]:
Judg 1:11	XJudges f1:4	q]ryt 	qIr√yÅt@np	1221
